In [698]:
# Import libraries
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from statsmodels.formula.api import ols
import shapefile
import geopandas as geo
import warnings

# Customize
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
warnings.filterwarnings("ignore")

# Approach

Summary of approach:

1. Data processing:

   - Import data from AEA RCT Registry
   - Filter data for Kenya
   - Text analysis to extract county information
   - Manual entry for missing county information
   - Match generic regions to counties
   - Create project-level and county-level datasets
   - Create datasets for restricted time period
   - Define coverage variable
   - Find total projects per county
   - Import data on outcome variables and merge with trials data
   - Repeat analysis for provinces

   
2. Descriptive analysis:
   - Summary statistics
   

3. Regression analysis:

   - Differences-in-differences model:
       - Education

# Data Processing 

## Import Data

- Data from [AEA RCT Registry](https://www.socialscienceregistry.org/trials/search): downloaded all 8327 projects reigstered on the site

In [699]:
# Import data on all trials from AEA
all_trials = pd.read_csv('all_trials.csv')
all_trials.head(5)

Title  \
0  Voter Pessimism and Electoral Accountability: ...   
1  Community Based Strategies to Reduce Maternal ...   
2  An Evaluation of Continuous Comprehensive Eval...   
3  Enhancing Local Public Service Delivery: Exper...   
4  Free DFS - Intervention to fight anemia and im...   

                                              Url  Last update date  \
0   http://www.socialscienceregistry.org/trials/5      May 02, 2017   
1   http://www.socialscienceregistry.org/trials/6  October 25, 2023   
2   http://www.socialscienceregistry.org/trials/8     June 15, 2013   
3   http://www.socialscienceregistry.org/trials/9  October 04, 2013   
4  http://www.socialscienceregistry.org/trials/10      May 15, 2013   

                Published at First registered on           RCT_ID  \
0  2017-05-02 16:17:17 -0400          2013-05-21  AEARCTR-0000005   
1  2023-10-25 15:31:05 -0400          2013-05-26  AEARCTR-0000006   
2  2013-06-15 09:00:16 -0400          2013-06-15  AEARCTR-0000008   
3  2013-10-04 16:31:22 -0400          2013-10-04  AEARCTR-0000009   
4  2013-05-15 10:14:16 -0400          2013-05-15  AEARCTR-0000010   

           DOI Number                         Primary Investigator     Status  \
0   10.1257/rct.5-8.0                  Kelly Zhang kwzhang@mit.edu  completed   
1   10.1257/rct.6-3.0  Vandana Sharma vsharma@povertyactionlab.org  completed   
2   10.1257/rct.8-1.0                 Esther  Duflo eduflo@mit.edu   on_going   
3   10.1257/rct.9-1.0                 Esther  Duflo eduflo@mit.edu   on_going   
4  10.1257/rct.10-1.0   Sharon Barnhardt sharonbarnhardt@gmail.com   on_going   

   Start date    End date                                           Keywords  \
0  2013-01-26  2014-05-31  ["electoral", "public goods", "corruption", "a...   
1  2012-02-01  2016-10-31  ["health", "pregnancy", "maternal mortality", ...   
2  2011-05-19  2014-12-31                ["education", "remedial education"]   
3  2012-01-01  2014-06-01            ["governance", "employment", "welfare"]   
4  2011-04-04  2014-06-01                  ["health", "Nutrition", "Anemia"]   

      Country names                        Other Primary Investigators  \
0  Kenya (National)                                                NaN   
1  Nigeria (Africa)  Martina Nyqvist (Martina.Bjorkman.Nyqvist@hhs....   
2           Private  Shobhini Mukerji (shobhini.mukerji@ifmr.ac.in)...   
3           Private  Abhijit Banerjee (banerjee@mit.edu) MIT, J-PAL...   
4           Private  Abhijit V. Banerjee (banerjee@mit.edu) MIT; Es...   

  Jel code                        Secondary IDs  \
0      NaN                                  NaN   
1      NaN  ClinicalTrials.gov ID: NCT01487707    
2      NaN                                  NaN   
3      NaN                                  NaN   
4      NaN                                  NaN   

                                            Abstract External Links Sponsors  \
0  The chapter combines novel survey, audit, and ...            NaN      NaN   
1  The objective of this cluster randomized contr...            NaN      NaN   
2  Under the Right to Education Act passed in 200...            NaN      NaN   
3  This project evaluates an innovative policy in...            NaN      NaN   
4  Iron deficiency anemia (IDA) has been linked t...            NaN      NaN   

  Partners Intervention start date Intervention end date  \
0      NaN              2013-03-02            2013-03-07   
1      NaN              2013-06-01            2015-06-01   
2      NaN              2011-11-30            2013-03-30   
3      NaN              2012-10-01            2013-04-01   
4      NaN              2013-05-11            2014-06-01   

                                        Intervention  \
0  The intervention was embedded within a series ...   
1  The study will be evaluating 3 primarily deman...   
2  There are two interventions:\r\n1) training te...   
3   In the new fund flow, the state pool of MNREG...   
4  We deliver free Double 

In [700]:
all_trials.shape

(8327, 50)

## Prepare Kenya Dataset

- Filter for trials specifically for Kenya
- Search for 'Kenya' in  `Country names`, `Abstract` or `Title`
    - Problem with searching in the abstract: lot of studies mention previous research done in Kenya, the study itself is not taking place in Kenya

In [701]:
kenya_trials = all_trials[all_trials['Country names'].str.contains('Kenya', na=False) | all_trials['Abstract'].str.contains('Kenya') | all_trials['Title'].str.contains('Kenya')]
kenya_trials.head()

Title  \
0   Voter Pessimism and Electoral Accountability: ...   
8   Understanding Ethnic Cooperation: Evidence fro...   
9     Welfare Effects of Unconditional Cash Transfers   
10    Welfare Effects of Unconditional Cash Transfers   
19  Electing to Vote: Strengthening the Credibilit...   

                                               Url   Last update date  \
0    http://www.socialscienceregistry.org/trials/5       May 02, 2017   
8   http://www.socialscienceregistry.org/trials/16       May 28, 2013   
9   http://www.socialscienceregistry.org/trials/17  December 08, 2020   
10  http://www.socialscienceregistry.org/trials/19      July 06, 2016   
19  http://www.socialscienceregistry.org/trials/30     April 20, 2014   

                 Published at First registered on           RCT_ID  \
0   2017-05-02 16:17:17 -0400          2013-05-21  AEARCTR-0000005   
8   2013-05-28 19:50:19 -0400          2013-05-28  AEARCTR-0000016   
9   2020-12-08 06:15:10 -0500          2014-12-04  AEARCTR-0000017   
10  2016-07-06 15:21:00 -0400          2013-06-28  AEARCTR-0000019   
19  2014-04-20 20:45:05 -0400          2014-04-20  AEARCTR-0000030   

            DOI Number                     Primary Investigator     Status  \
0    10.1257/rct.5-8.0              Kelly Zhang kwzhang@mit.edu  completed   
8   10.1257/rct.16-1.0  Edward Miguel emiguel@econ.berkeley.edu  completed   
9   10.1257/rct.17-1.1   Johannes Haushofer haushofer@gmail.com  completed   
10  10.1257/rct.19-5.0   Johannes Haushofer haushofer@gmail.com  completed   
19  10.1257/rct.30-1.0             Tavneet Suri tavneet@mit.edu   on_going   

    Start date    End date                                           Keywords  \
0   2013-01-26  2014-05-31  ["electoral", "public goods", "corruption", "a...   
8   2012-07-16  2013-02-14  ["electoral", "governance", "post-conflict", "...   
9   2011-05-01  2013-02-28  ["agriculture", "education", "finance", "healt...   
10  2011-05-01  2013-02-28  ["agriculture", "education", "finance", "healt...   
19  2013-02-19  2014-12-01  ["electoral", "governance", "post-conflict", "...   

                                Country names  \
0                            Kenya (National)   
8   Kenya (); Tanzania, United Republic of ()   
9                             Kenya (Rarieda)   
10                            Kenya (Rarieda)   
19                                    Private   

                          Other Primary Investigators  \
0                                                 NaN   
8   Kelly Zhang () Stanford University; Bertil Tun...   
9   Jeremy Shapiro (jeremypshapiro@gmail.com) Prin...   
10  Jeremy Shapiro (jeremypshapiro@gmail.com) McKi...   
19  Vincent Pons (vpons@mit.edu) MIT; Benjamin Mar...   

                   Jel code Secondary IDs  \
0                       NaN           NaN   
8                       NaN           NaN   
9   C93, D13, I15, I25, O12           NaN   
10  C93, D13, I15, I25, O12           NaN   
19                      NaN           NaN   

                                             Abstract External Links Sponsors  \
0   The chapter combines novel survey, audit, and ...            NaN      NaN   
8   Ethnic polarization is often linked to underde...            NaN      NaN   
9   This randomized controlled trial (RCT) evaluat...            NaN      NaN   
10  This randomized controlled trial (RCT) evaluat...            NaN      NaN   
19  This study analyzes the impact of different se...            NaN      NaN   

   Partners Intervention start date Intervention end date  \
0       NaN              2013-03-02            2013-03-07   
8       NaN              2012-07-16            2013-02-14   
9       NaN              2011-06-01            2013-01-31   
10      NaN              2011-06-01            2013-01-31   
19      NaN              2013-02-28            2013-03-04   

                                         Intervention  \
0   The intervention was embedded within a series ...   
8   Differen

In [702]:
kenya_trials.shape

# 250 trials related to Kenya

(250, 50)

- <font color='green'> AEA website shows that there are 279 trials related to Kenya - which trials are left out? How to find them? </font>

In [703]:
# Look at country names
kenya_trials['Country names']

0                                        Kenya (National)
8               Kenya (); Tanzania, United Republic of ()
9                                         Kenya (Rarieda)
10                                        Kenya (Rarieda)
19                                                Private
44                                                Private
67                  Kenya (Meru & Tharaka-Nithi Counties)
100                                               Private
125                                       Kenya (Nairobi)
157              Kenya (Kakamega, Kisii, Embu and Kitui )
160                 Tanzania, United Republic of (Africa)
175                                               Private
193                                  Kenya (Busia, Siaya)
237                                               Private
243                                               Private
255                                               Private
270                                       Kenya (Western)
283           

In [704]:
# Regular expressions to extract name of county + add to the dataframe
pat_1 = r'Kenya\s*\(([\w\s\-\&\,]*)\)'
counties = kenya_trials['Country names'].str.findall(pat_1).fillna('')
counties_col = []
for i in range(len(counties)):
    if len(counties.iloc[i]) > 0:
        counties_col.append(counties.iloc[i][0])
    else:
        counties_col.append('')
kenya_trials['County'] = counties_col

In [705]:
kenya_trials['County']

0                                                National
8                                                        
9                                                 Rarieda
10                                                Rarieda
19                                                       
44                                                       
67                          Meru & Tharaka-Nithi Counties
100                                                      
125                                               Nairobi
157                      Kakamega, Kisii, Embu and Kitui 
160                                                      
175                                                      
193                                          Busia, Siaya
237                                                      
243                                                      
255                                                      
270                                               Western
283           

In [706]:
# Export dataframe - fill in the missing counties manually
kenya_trials.to_csv('kenya_trials.csv')

- Need to compare existing spreadsheet and match to find new projects
- Sort both RCT_IDs and insert the new projects at points of mismatch

In [707]:
# Importing missing counties data with new manually entered information
missing_counties_data = pd.read_csv('missing_counties_data.csv')
missing_counties_data.shape

(241, 2)

In [708]:
# Merge Kenya trials data with new counties data
kenya_trials = kenya_trials.merge(missing_counties_data, on='RCT_ID', how='left')
kenya_trials

Title  \
0    Voter Pessimism and Electoral Accountability: ...   
1    Understanding Ethnic Cooperation: Evidence fro...   
2      Welfare Effects of Unconditional Cash Transfers   
3      Welfare Effects of Unconditional Cash Transfers   
4    Electing to Vote: Strengthening the Credibilit...   
5    Understanding smallholder arbitrage in Kenyan ...   
6    Mitigating Aflatoxin Exposure to Improve Child...   
7    THE IMPACT OF VCT AND CONDOM DISTRIBUTION AS H...   
8    The effect of acute stress on productivity, ti...   
9    Unpacking the determinants of entrepreneurship...   
10   Promoting Early Grade Reading & Numeracy in Ta...   
11   Increasing Savings for Vulnerable Women’s Empo...   
12   Evaluation of Mass Electricity Connections in ...   
13   High Hopes: Saving for High School with a Mobi...   
14   Evaluating the Socio-economic Impacts of   Wes...   
15   Estimating the Impacts of Microfranchising on ...   
16         Agricultural insurance and contract farming   
17   General Equilibrium Effects of Cash Transfers ...   
18   Interlinked Transactions, Saving Constraints, ...   
19   Evaluating Alternative Cash Transfer Designs i...   
20   Zusha! A randomized behavior change road safet...   
21   Impact Evaluation of Scaling Up Sweet potato T...   
22   Moral Hazard, Networks and Risk Sharing: Evide...   
23   Mental Health in the Developing World: Using P...   
24                          Start-up Capital for Youth   
25   Urban Micro-Insurance Project Evaluation: Pre-...   
26   Soapy Water Handwashing Stations School Pilot ...   
27   Willingness to Pay for Soapy Water Handwashing...   
28   Evaluating the impact of targeted health mobil...   
29                Can Health Insurance Reduce Poverty?   
30   Intergenerational Impacts of Health Investment...   
31   The Effect of Savings Accounts on Interpersona...   
32   The Effect of Atheism Primes on Self-reported ...   
33   Is female empowerment always good for child we...   
34   Welfare, Work, and Wellbeing: Evidence from an...   
35                      Poverty and Cognitive Function   
36   Examining Poverty and Anti-Social Behavior in ...   
37   The Effects of Child Care Subsidies on Women’s...   
38   Measuring the Effects of Child Care Subsidies ...   
39                Using Lotteries to Encourage Savings   
40   The effect of fear of violence on cognition an...   
41   Adoption and Impact of Low Cost Solar Energy: ...   
42   Effect of Experimentally Induced Stress on Tem...   
43            Kenyan Judicial Performance Improvement    
44   An Economic Analysis of Gender Inequalities in...   
45    Demand for Aflatoxin-Tested Maize Flour in Kenya   
46         Adolescent Girls Initiative - Kenya (AGI-K)   
47   Short-Term Economic Effects of Psychological A...   
48   Direct and Interaction Effects of Cash Transfe...   
49              Kenya Patient Safety Impact Evaluation   
50           KickStart Impact Evaluation: Cohort Study   
51   Light-Touch Social Psychology Interventions an...   
52   Spring Cleaning: Rural Water Impacts, Valuatio...   
53   Water Treatement Promotion at Health Clinics i...   
54   Worms: Identifying Impacts on Education and He...   
55                      The Illusion of Sustainability   
56   Price Subsidies, Diagnostic Tests, and Targeti...   
57   Free distribution or cost-sharing? Evidence fr...   
58   Why Don’t the Poor Save More? Evidence from He...   
59                            Education as Liberation?   
60   Evaluating the impacts of WorkShop access for ...   
61   Experimental Evidence on Child Health and Long...   
62   Keeping the Doctor Away: Experimental Evidence...   
63   The Causal Impact of the Judiciary on Economic...   
64   Peer Effects, Pupil-Teacher Ratios, and Teache...   
65       Examining Barriers to Fertilizer Use in Kenya   
66   Do Opposites Detract? Intrahousehold Preferenc...   
67                    Temperature and Economic Choices   
68   Benchmarking development programs: a prefe

In [709]:
# Replace NaN values in new counties column for text analysis
kenya_trials['County_y'] = kenya_trials['County_y'].fillna('')

In [710]:
# Create new counties column based on the existing 2
final_counties = []
for i in range(len(kenya_trials)):
    x = kenya_trials['County_x'].iloc[i]
    y = kenya_trials['County_y'].iloc[i]
    if x == '':
        final_counties.append(y)
    elif y == '':
        final_counties.append(x)
    else:
        final_counties.append(y)

# Create new column with final county values
kenya_trials['County'] = final_counties
kenya_trials.head()

Title  \
0  Voter Pessimism and Electoral Accountability: ...   
1  Understanding Ethnic Cooperation: Evidence fro...   
2    Welfare Effects of Unconditional Cash Transfers   
3    Welfare Effects of Unconditional Cash Transfers   
4  Electing to Vote: Strengthening the Credibilit...   

                                              Url   Last update date  \
0   http://www.socialscienceregistry.org/trials/5       May 02, 2017   
1  http://www.socialscienceregistry.org/trials/16       May 28, 2013   
2  http://www.socialscienceregistry.org/trials/17  December 08, 2020   
3  http://www.socialscienceregistry.org/trials/19      July 06, 2016   
4  http://www.socialscienceregistry.org/trials/30     April 20, 2014   

                Published at First registered on           RCT_ID  \
0  2017-05-02 16:17:17 -0400          2013-05-21  AEARCTR-0000005   
1  2013-05-28 19:50:19 -0400          2013-05-28  AEARCTR-0000016   
2  2020-12-08 06:15:10 -0500          2014-12-04  AEARCTR-0000017   
3  2016-07-06 15:21:00 -0400          2013-06-28  AEARCTR-0000019   
4  2014-04-20 20:45:05 -0400          2014-04-20  AEARCTR-0000030   

           DOI Number                     Primary Investigator     Status  \
0   10.1257/rct.5-8.0              Kelly Zhang kwzhang@mit.edu  completed   
1  10.1257/rct.16-1.0  Edward Miguel emiguel@econ.berkeley.edu  completed   
2  10.1257/rct.17-1.1   Johannes Haushofer haushofer@gmail.com  completed   
3  10.1257/rct.19-5.0   Johannes Haushofer haushofer@gmail.com  completed   
4  10.1257/rct.30-1.0             Tavneet Suri tavneet@mit.edu   on_going   

   Start date    End date                                           Keywords  \
0  2013-01-26  2014-05-31  ["electoral", "public goods", "corruption", "a...   
1  2012-07-16  2013-02-14  ["electoral", "governance", "post-conflict", "...   
2  2011-05-01  2013-02-28  ["agriculture", "education", "finance", "healt...   
3  2011-05-01  2013-02-28  ["agriculture", "education", "finance", "healt...   
4  2013-02-19  2014-12-01  ["electoral", "governance", "post-conflict", "...   

                               Country names  \
0                           Kenya (National)   
1  Kenya (); Tanzania, United Republic of ()   
2                            Kenya (Rarieda)   
3                            Kenya (Rarieda)   
4                                    Private   

                         Other Primary Investigators                 Jel code  \
0                                                NaN                      NaN   
1  Kelly Zhang () Stanford University; Bertil Tun...                      NaN   
2  Jeremy Shapiro (jeremypshapiro@gmail.com) Prin...  C93, D13, I15, I25, O12   
3  Jeremy Shapiro (jeremypshapiro@gmail.com) McKi...  C93, D13, I15, I25, O12   
4  Vincent Pons (vpons@mit.edu) MIT; Benjamin Mar...                      NaN   

  Secondary IDs                                           Abstract  \
0           NaN  The chapter combines novel survey, audit, and ...   
1           NaN  Ethnic polarization is often linked to underde...   
2           NaN  This randomized controlled trial (RCT) evaluat...   
3           NaN  This randomized controlled trial (RCT) evaluat...   
4           NaN  This study analyzes the impact of different se...   

  External Links Sponsors Partners Intervention start date  \
0            NaN      NaN      NaN              2013-03-02   
1            NaN      NaN      NaN              2012-07-16   
2            NaN      NaN      NaN              2011-06-01   
3            NaN      NaN      NaN              2011-06-01   
4            NaN      NaN      NaN              2013-02-28   

  Intervention end date                                       Intervention  \
0            2013-03-07  The intervention was embedded within a series ...   
1            2013-02-14  Different subject priming treatments in the la...   
2            2013-01-31  The UCT Program implemented by GiveDirectly In...   
3            2013-01-31  The UCT Pro

In [711]:
# Number of trials with no county information
sum(kenya_trials['County'] == '')

85

In [712]:
kenya_trials.columns

Index(['Title', 'Url', 'Last update date', 'Published at',
       'First registered on', 'RCT_ID', 'DOI Number', 'Primary Investigator',
       'Status', 'Start date', 'End date', 'Keywords', 'Country names',
       'Other Primary Investigators', 'Jel code', 'Secondary IDs', 'Abstract',
       'External Links', 'Sponsors', 'Partners', 'Intervention start date',
       'Intervention end date', 'Intervention', 'Primary outcome end points',
       'Primary outcome explanation', 'Secondary outcome end points',
       'Secondary outcome explanation', 'Experimental design',
       'Experimental design details', 'Randomization method',
       'Randomization unit', 'Sample size number clusters',
       'Sample size number observations', 'Sample size number arms',
       'Minimum effect size', 'IRB', 'Analysis Plan Documents',
       'Intervention completion date', 'Data collection completion',
       'Data collection completion date', 'Number of clusters',
       'Attrition correlated', 'Total

In [713]:
# Remove entries with no county information and select relevant columns
kenya_trials_final = kenya_trials[kenya_trials['County'] != ''][['RCT_ID', 'Start date', 'End date', 'Keywords', 'County']]
kenya_trials_final.shape

(165, 5)

In [714]:
kenya_trials_final = kenya_trials_final[(kenya_trials_final['County'] != 'National') & (kenya_trials_final['County'] != 'Africa') & (kenya_trials_final['County'] != 'District of Columbia') & (kenya_trials_final['County'] != 'sub-Saharan Africa')]
kenya_trials_final

RCT_ID  Start date    End date  \
1    AEARCTR-0000016  2012-07-16  2013-02-14   
2    AEARCTR-0000017  2011-05-01  2013-02-28   
3    AEARCTR-0000019  2011-05-01  2013-02-28   
5    AEARCTR-0000067  2012-08-01  2014-08-15   
6    AEARCTR-0000105  2013-02-01  2017-03-31   
8    AEARCTR-0000218  2013-05-28  2013-08-07   
9    AEARCTR-0000287  2013-06-01  2018-06-01   
11   AEARCTR-0000323  2014-01-27  2014-10-26   
12   AEARCTR-0000350  2014-02-07  2020-08-31   
14   AEARCTR-0000443  2013-12-10  2016-06-30   
15   AEARCTR-0000459  2013-05-31  2015-12-31   
16   AEARCTR-0000486  2014-08-25  2015-08-25   
19   AEARCTR-0000541  2014-11-10  2016-04-30   
22   AEARCTR-0000605  2015-01-28  2015-08-15   
23   AEARCTR-0000627  2014-11-01  2014-12-31   
25   AEARCTR-0000647  2011-03-01  2013-04-30   
26   AEARCTR-0000662  2015-05-04  2016-09-15   
27   AEARCTR-0000669  2015-04-14  2016-09-15   
28   AEARCTR-0000676  2015-04-08  2016-12-31   
29   AEARCTR-0000705  2010-10-01  2014-06-01   
31   AEARCTR-0000740  2009-08-01  2015-06-18   
32   AEARCTR-0000766  2015-04-25  2015-06-15   
34   AEARCTR-0000788  2014-09-15  2016-01-01   
35   AEARCTR-0000790  2015-06-29  2015-09-01   
36   AEARCTR-0000791  2015-02-01  2015-07-01   
37   AEARCTR-0000843  2015-09-15  2018-08-31   
38   AEARCTR-0000844  2015-09-15  2017-03-22   
39   AEARCTR-0000893  2014-05-01  2014-08-01   
40   AEARCTR-0000907  2015-10-08  2015-11-30   
41   AEARCTR-0000912  2015-06-11  2016-04-01   
42   AEARCTR-0000934  2013-02-01  2015-12-31   
44   AEARCTR-0000946  2011-03-01  2013-01-31   
46   AEARCTR-0000962  2015-01-13  2019-12-31   
47   AEARCTR-0000991  2015-07-01  2016-06-01   
48   AEARCTR-0000996  2016-01-11  2024-12-31   
50   AEARCTR-0001002  2010-01-01  2016-03-01   
51   AEARCTR-0001008  2015-10-01  2016-01-01   
53   AEARCTR-0001076  2007-11-12  2010-08-31   
57   AEARCTR-0001167  2007-02-01  2007-08-31   
59   AEARCTR-0001183  2005-10-01  2007-02-28   
60   AEARCTR-0001187  2016-06-01  2018-04-01   
62   AEARCTR-0001197  2010-01-01  2010-05-31   
63   AEARCTR-0001293  2014-06-01  2018-01-01   
64   AEARCTR-0001304  2005-03-01  2007-11-30   
66   AEARCTR-0001358  2009-05-01  2012-12-31   
69   AEARCTR-0001373  2017-04-03  2018-07-31   
70   AEARCTR-0001432  2003-02-01  2011-03-31   
71   AEARCTR-0001457  2015-06-01  2015-11-28   
72   AEARCTR-0001482  2016-01-01  2017-08-01   
73   AEARCTR-0001484  2016-07-04  2020-12-31   
74   AEARCTR-0001500  2016-09-19  2017-12-31   
75   AEARCTR-0001515  2015-01-01  2016-07-01   
76   AEARCTR-0001574  2016-09-14  2016-09-26   
77   AEARCTR-0001592  2006-02-01  2013-01-01   
78   AEARCTR-0001643  2016-09-05  2017-12-31   
79   AEARCTR-0001706  2009-10-01  2014-01-15   
80   AEARCTR-0001748  2003-01-01  2005-12-31   
81   AEARCTR-0001750  2000-06-01  2003-09-30   
82   AEARCTR-0001812  2003-12-01  2005-05-31   
83   AEARCTR-0001824  2009-07-01  2013-08-31   
85   AEARCTR-0001848  2015-03-13  2015-08-10   
86   AEARCTR-0001893  2006-04-01  2006-10-31   
87   AEARCTR-0001902  2016-08-25  2017-05-15   
89   AEARCTR-0001997  2016-11-07  2017-01-29   
90   AEARCTR-0002015  2016-06-01  2018-03-31   
91   AEARCTR-0002019  2016-08-01  2017-12-31   
92   AEARCTR-0002026  2015-03-02  2015-05-08   
93   AEARCTR-0002063  2014-06-01  2017-12-31   
94   AEARCTR-0002071  2016-11-16  2017-03-01   
95   AEARCTR-0002133  2015-03-01  2019-08-05   
97   AEARCTR-0002188  2015-08-01  2016-11-30   
98   AEARCTR-0002313  2015-06-01  2017-10-30   
100  AEARCTR-0002370  2014-01-01  2017-07-30   
101  AEARCTR-0002375  2017-07-12  2017-08-05   
103  AEARCTR-0002401  2017-07-03  2017-12-31   
104  AEARCTR-0002448  2017-09-25  2018-09-25   
105  AEARCTR-0002484  2017-10-01  2023-12-31   
107  AEARCTR-0002579  2016-05-01  2019-06-30   
108  AEARCTR-0002692  2018-05-28  2020-02-01   
109  AEARCTR-0002741  2017-02-15  2017-12-13   
110  AEARCTR-0002850  2017-10-01  2021-02-01   
111  AEARCTR-0002913  2017-08-03  2022-05-31   
113  AEARCTR-0002923  2016-11-

- Some of the locations entered are cities, which must be replaced with the counties they are in as this is a county-level analysis

In [715]:
# Replace some words
kenya_trials_final['County'] = kenya_trials_final['County'].str.replace('Rarieda', 'Siaya')
kenya_trials_final['County'] = kenya_trials_final['County'].str.replace('Butere', 'Kakamega')
kenya_trials_final['County'] = kenya_trials_final['County'].str.replace('Mumias', 'Kakamega')
kenya_trials_final['County'] = kenya_trials_final['County'].str.replace('Samia', 'Busia')
kenya_trials_final['County'] = kenya_trials_final['County'].str.replace('Nambale', 'Busia')
kenya_trials_final['County'] = kenya_trials_final['County'].str.replace('Ndaragwa', 'Nyandarua')
kenya_trials_final['County'] = kenya_trials_final['County'].str.replace('Transnzoia', 'Trans Nzoia')
kenya_trials_final['County'] = kenya_trials_final['County'].str.replace('Dandora', 'Nairobi')
kenya_trials_final['County'] = kenya_trials_final['County'].str.replace('Makeuni', 'Makueni')
kenya_trials_final['County'] = kenya_trials_final['County'].str.replace('Tharaka Nithi', 'Tharaka-Nithi')
kenya_trials_final['County'] = kenya_trials_final['County'].str.replace('Kibera', 'Nairobi')
kenya_trials_final['County'] = kenya_trials_final['County'].str.replace('Mount Kenya Region', 'Eastern, Central')
kenya_trials_final['County'] = kenya_trials_final['County'].str.replace('Eastern and Western Kenya', 'Eastern, Western')

In [716]:
# Get list of county names and their provinces
counties = pd.read_csv('counties.csv')
counties

County     Province
0           Mombasa        Coast
1             Kwale        Coast
2            Kilifi        Coast
3        Tana River        Coast
4              Lamu        Coast
5      Taita-Taveta        Coast
6           Garissa     Northern
7             Wajir     Northern
8           Mandera     Northern
9          Marsabit      Eastern
10           Isiolo      Eastern
11             Meru      Eastern
12    Tharaka-Nithi      Eastern
13             Embu      Eastern
14            Kitui      Eastern
15         Machakos      Eastern
16          Makueni      Eastern
17        Nyandarua      Central
18            Nyeri      Central
19        Kirinyaga      Central
20         Murang'a      Central
21           Kiambu      Central
22          Turkana  Rift Valley
23       West Pokot  Rift Valley
24          Samburu  Rift Valley
25      Trans Nzoia  Rift Valley
26      Uasin Gishu  Rift Valley
27  Elgeyo-Marakwet  Rift Valley
28            Nandi  Rift Valley
29          Baringo  Rift Valley
30         Laikipia  Rift Valley
31           Nakuru  Rift Valley
32            Narok  Rift Valley
33          Kajiado  Rift Valley
34          Kericho  Rift Valley
35            Bomet  Rift Valley
36         Kakamega      Western
37           Vihiga      Western
38          Bungoma      Western
39            Busia      Western
40            Siaya       Nyanza
41           Kisumu       Nyanza
42         Homa Bay       Nyanza
43           Migori       Nyanza
44            Kisii       Nyanza
45          Nyamira       Nyanza
46          Nairobi      Nairobi

In [717]:
# Changing general region names to specific ones
regions = np.array(counties['Province'].value_counts().index)

for i in kenya_trials_final.index:
    temp_list = []
    county = kenya_trials_final['County'].loc[i].split(',')
    for j in county:
        if j.strip() in regions:
            temp_list.extend(list(counties[counties['Province'] == j.strip()]['County']))
        else:
            temp_list.append(j)
    kenya_trials_final.at[i, 'County'] = temp_list

In [718]:
kenya_trials_final

RCT_ID  Start date    End date  \
1    AEARCTR-0000016  2012-07-16  2013-02-14   
2    AEARCTR-0000017  2011-05-01  2013-02-28   
3    AEARCTR-0000019  2011-05-01  2013-02-28   
5    AEARCTR-0000067  2012-08-01  2014-08-15   
6    AEARCTR-0000105  2013-02-01  2017-03-31   
8    AEARCTR-0000218  2013-05-28  2013-08-07   
9    AEARCTR-0000287  2013-06-01  2018-06-01   
11   AEARCTR-0000323  2014-01-27  2014-10-26   
12   AEARCTR-0000350  2014-02-07  2020-08-31   
14   AEARCTR-0000443  2013-12-10  2016-06-30   
15   AEARCTR-0000459  2013-05-31  2015-12-31   
16   AEARCTR-0000486  2014-08-25  2015-08-25   
19   AEARCTR-0000541  2014-11-10  2016-04-30   
22   AEARCTR-0000605  2015-01-28  2015-08-15   
23   AEARCTR-0000627  2014-11-01  2014-12-31   
25   AEARCTR-0000647  2011-03-01  2013-04-30   
26   AEARCTR-0000662  2015-05-04  2016-09-15   
27   AEARCTR-0000669  2015-04-14  2016-09-15   
28   AEARCTR-0000676  2015-04-08  2016-12-31   
29   AEARCTR-0000705  2010-10-01  2014-06-01   
31   AEARCTR-0000740  2009-08-01  2015-06-18   
32   AEARCTR-0000766  2015-04-25  2015-06-15   
34   AEARCTR-0000788  2014-09-15  2016-01-01   
35   AEARCTR-0000790  2015-06-29  2015-09-01   
36   AEARCTR-0000791  2015-02-01  2015-07-01   
37   AEARCTR-0000843  2015-09-15  2018-08-31   
38   AEARCTR-0000844  2015-09-15  2017-03-22   
39   AEARCTR-0000893  2014-05-01  2014-08-01   
40   AEARCTR-0000907  2015-10-08  2015-11-30   
41   AEARCTR-0000912  2015-06-11  2016-04-01   
42   AEARCTR-0000934  2013-02-01  2015-12-31   
44   AEARCTR-0000946  2011-03-01  2013-01-31   
46   AEARCTR-0000962  2015-01-13  2019-12-31   
47   AEARCTR-0000991  2015-07-01  2016-06-01   
48   AEARCTR-0000996  2016-01-11  2024-12-31   
50   AEARCTR-0001002  2010-01-01  2016-03-01   
51   AEARCTR-0001008  2015-10-01  2016-01-01   
53   AEARCTR-0001076  2007-11-12  2010-08-31   
57   AEARCTR-0001167  2007-02-01  2007-08-31   
59   AEARCTR-0001183  2005-10-01  2007-02-28   
60   AEARCTR-0001187  2016-06-01  2018-04-01   
62   AEARCTR-0001197  2010-01-01  2010-05-31   
63   AEARCTR-0001293  2014-06-01  2018-01-01   
64   AEARCTR-0001304  2005-03-01  2007-11-30   
66   AEARCTR-0001358  2009-05-01  2012-12-31   
69   AEARCTR-0001373  2017-04-03  2018-07-31   
70   AEARCTR-0001432  2003-02-01  2011-03-31   
71   AEARCTR-0001457  2015-06-01  2015-11-28   
72   AEARCTR-0001482  2016-01-01  2017-08-01   
73   AEARCTR-0001484  2016-07-04  2020-12-31   
74   AEARCTR-0001500  2016-09-19  2017-12-31   
75   AEARCTR-0001515  2015-01-01  2016-07-01   
76   AEARCTR-0001574  2016-09-14  2016-09-26   
77   AEARCTR-0001592  2006-02-01  2013-01-01   
78   AEARCTR-0001643  2016-09-05  2017-12-31   
79   AEARCTR-0001706  2009-10-01  2014-01-15   
80   AEARCTR-0001748  2003-01-01  2005-12-31   
81   AEARCTR-0001750  2000-06-01  2003-09-30   
82   AEARCTR-0001812  2003-12-01  2005-05-31   
83   AEARCTR-0001824  2009-07-01  2013-08-31   
85   AEARCTR-0001848  2015-03-13  2015-08-10   
86   AEARCTR-0001893  2006-04-01  2006-10-31   
87   AEARCTR-0001902  2016-08-25  2017-05-15   
89   AEARCTR-0001997  2016-11-07  2017-01-29   
90   AEARCTR-0002015  2016-06-01  2018-03-31   
91   AEARCTR-0002019  2016-08-01  2017-12-31   
92   AEARCTR-0002026  2015-03-02  2015-05-08   
93   AEARCTR-0002063  2014-06-01  2017-12-31   
94   AEARCTR-0002071  2016-11-16  2017-03-01   
95   AEARCTR-0002133  2015-03-01  2019-08-05   
97   AEARCTR-0002188  2015-08-01  2016-11-30   
98   AEARCTR-0002313  2015-06-01  2017-10-30   
100  AEARCTR-0002370  2014-01-01  2017-07-30   
101  AEARCTR-0002375  2017-07-12  2017-08-05   
103  AEARCTR-0002401  2017-07-03  2017-12-31   
104  AEARCTR-0002448  2017-09-25  2018-09-25   
105  AEARCTR-0002484  2017-10-01  2023-12-31   
107  AEARCTR-0002579  2016-05-01  2019-06-30   
108  AEARCTR-0002692  2018-05-28  2020-02-01   
109  AEARCTR-0002741  2017-02-15  2017-12-13   
110  AEARCTR-0002850  2017-10-01  2021-02-01   
111  AEARCTR-0002913  2017-08-03  2022-05-31   
113  AEARCTR-0002923  2016-11-

In [719]:
kenya_trials_final.shape

(154, 5)

In [720]:
# Add province information
provinces = []
for i in kenya_trials_final.index:
    temp_list = []
    county = kenya_trials_final['County'].loc[i]
    for j in county:
        val = counties[counties['County'] == j.strip()]['Province'].iloc[0]
        if val not in temp_list:
            temp_list.append(val)
    provinces.append(temp_list)
provinces

[['Nairobi'],
 ['Nyanza'],
 ['Nyanza'],
 ['Western'],
 ['Eastern'],
 ['Nairobi'],
 ['Western', 'Nyanza', 'Eastern'],
 ['Nyanza'],
 ['Western', 'Nyanza'],
 ['Western', 'Nyanza', 'Central'],
 ['Nairobi'],
 ['Western'],
 ['Nyanza'],
 ['Nairobi'],
 ['Nairobi'],
 ['Nairobi'],
 ['Nyanza'],
 ['Nyanza'],
 ['Nairobi'],
 ['Central'],
 ['Western'],
 ['Nairobi'],
 ['Nairobi'],
 ['Nairobi'],
 ['Nairobi'],
 ['Nairobi'],
 ['Nairobi'],
 ['Nairobi'],
 ['Nairobi'],
 ['Western'],
 ['Nairobi'],
 ['Western'],
 ['Northern', 'Nairobi'],
 ['Western'],
 ['Nyanza'],
 ['Nairobi'],
 ['Nyanza'],
 ['Western'],
 ['Western'],
 ['Western'],
 ['Nairobi'],
 ['Western'],
 ['Central'],
 ['Western'],
 ['Western'],
 ['Eastern'],
 ['Western'],
 ['Nairobi'],
 ['Nairobi'],
 ['Western'],
 ['Nairobi'],
 ['Northern'],
 ['Western'],
 ['Western'],
 ['Western'],
 ['Western'],
 ['Western'],
 ['Western'],
 ['Central'],
 ['Western'],
 ['Rift Valley', 'Eastern'],
 ['Western', 'Nyanza'],
 ['Nairobi'],
 ['Nairobi'],
 ['Eastern'],
 ['Easte

In [721]:
kenya_trials_final['Province'] = provinces

In [722]:
kenya_trials_final

RCT_ID  Start date    End date  \
1    AEARCTR-0000016  2012-07-16  2013-02-14   
2    AEARCTR-0000017  2011-05-01  2013-02-28   
3    AEARCTR-0000019  2011-05-01  2013-02-28   
5    AEARCTR-0000067  2012-08-01  2014-08-15   
6    AEARCTR-0000105  2013-02-01  2017-03-31   
8    AEARCTR-0000218  2013-05-28  2013-08-07   
9    AEARCTR-0000287  2013-06-01  2018-06-01   
11   AEARCTR-0000323  2014-01-27  2014-10-26   
12   AEARCTR-0000350  2014-02-07  2020-08-31   
14   AEARCTR-0000443  2013-12-10  2016-06-30   
15   AEARCTR-0000459  2013-05-31  2015-12-31   
16   AEARCTR-0000486  2014-08-25  2015-08-25   
19   AEARCTR-0000541  2014-11-10  2016-04-30   
22   AEARCTR-0000605  2015-01-28  2015-08-15   
23   AEARCTR-0000627  2014-11-01  2014-12-31   
25   AEARCTR-0000647  2011-03-01  2013-04-30   
26   AEARCTR-0000662  2015-05-04  2016-09-15   
27   AEARCTR-0000669  2015-04-14  2016-09-15   
28   AEARCTR-0000676  2015-04-08  2016-12-31   
29   AEARCTR-0000705  2010-10-01  2014-06-01   
31   AEARCTR-0000740  2009-08-01  2015-06-18   
32   AEARCTR-0000766  2015-04-25  2015-06-15   
34   AEARCTR-0000788  2014-09-15  2016-01-01   
35   AEARCTR-0000790  2015-06-29  2015-09-01   
36   AEARCTR-0000791  2015-02-01  2015-07-01   
37   AEARCTR-0000843  2015-09-15  2018-08-31   
38   AEARCTR-0000844  2015-09-15  2017-03-22   
39   AEARCTR-0000893  2014-05-01  2014-08-01   
40   AEARCTR-0000907  2015-10-08  2015-11-30   
41   AEARCTR-0000912  2015-06-11  2016-04-01   
42   AEARCTR-0000934  2013-02-01  2015-12-31   
44   AEARCTR-0000946  2011-03-01  2013-01-31   
46   AEARCTR-0000962  2015-01-13  2019-12-31   
47   AEARCTR-0000991  2015-07-01  2016-06-01   
48   AEARCTR-0000996  2016-01-11  2024-12-31   
50   AEARCTR-0001002  2010-01-01  2016-03-01   
51   AEARCTR-0001008  2015-10-01  2016-01-01   
53   AEARCTR-0001076  2007-11-12  2010-08-31   
57   AEARCTR-0001167  2007-02-01  2007-08-31   
59   AEARCTR-0001183  2005-10-01  2007-02-28   
60   AEARCTR-0001187  2016-06-01  2018-04-01   
62   AEARCTR-0001197  2010-01-01  2010-05-31   
63   AEARCTR-0001293  2014-06-01  2018-01-01   
64   AEARCTR-0001304  2005-03-01  2007-11-30   
66   AEARCTR-0001358  2009-05-01  2012-12-31   
69   AEARCTR-0001373  2017-04-03  2018-07-31   
70   AEARCTR-0001432  2003-02-01  2011-03-31   
71   AEARCTR-0001457  2015-06-01  2015-11-28   
72   AEARCTR-0001482  2016-01-01  2017-08-01   
73   AEARCTR-0001484  2016-07-04  2020-12-31   
74   AEARCTR-0001500  2016-09-19  2017-12-31   
75   AEARCTR-0001515  2015-01-01  2016-07-01   
76   AEARCTR-0001574  2016-09-14  2016-09-26   
77   AEARCTR-0001592  2006-02-01  2013-01-01   
78   AEARCTR-0001643  2016-09-05  2017-12-31   
79   AEARCTR-0001706  2009-10-01  2014-01-15   
80   AEARCTR-0001748  2003-01-01  2005-12-31   
81   AEARCTR-0001750  2000-06-01  2003-09-30   
82   AEARCTR-0001812  2003-12-01  2005-05-31   
83   AEARCTR-0001824  2009-07-01  2013-08-31   
85   AEARCTR-0001848  2015-03-13  2015-08-10   
86   AEARCTR-0001893  2006-04-01  2006-10-31   
87   AEARCTR-0001902  2016-08-25  2017-05-15   
89   AEARCTR-0001997  2016-11-07  2017-01-29   
90   AEARCTR-0002015  2016-06-01  2018-03-31   
91   AEARCTR-0002019  2016-08-01  2017-12-31   
92   AEARCTR-0002026  2015-03-02  2015-05-08   
93   AEARCTR-0002063  2014-06-01  2017-12-31   
94   AEARCTR-0002071  2016-11-16  2017-03-01   
95   AEARCTR-0002133  2015-03-01  2019-08-05   
97   AEARCTR-0002188  2015-08-01  2016-11-30   
98   AEARCTR-0002313  2015-06-01  2017-10-30   
100  AEARCTR-0002370  2014-01-01  2017-07-30   
101  AEARCTR-0002375  2017-07-12  2017-08-05   
103  AEARCTR-0002401  2017-07-03  2017-12-31   
104  AEARCTR-0002448  2017-09-25  2018-09-25   
105  AEARCTR-0002484  2017-10-01  2023-12-31   
107  AEARCTR-0002579  2016-05-01  2019-06-30   
108  AEARCTR-0002692  2018-05-28  2020-02-01   
109  AEARCTR-0002741  2017-02-15  2017-12-13   
110  AEARCTR-0002850  2017-10-01  2021-02-01   
111  AEARCTR-0002913  2017-08-03  2022-05-31   
113  AEARCTR-0002923  2016-11-

In [723]:
# Create dataframe of dummy variables per project
df_by_project = pd.DataFrame(columns=counties['County'])
for i in range(len(kenya_trials_final['County'])):
    temp_list = []
    for j in counties['County']:
        if (j in kenya_trials_final['County'].iloc[i]):
            temp_list.append(1)
        else:
            temp_list.append(0)
    df_by_project.loc[kenya_trials_final['RCT_ID'].iloc[i]] = temp_list

In [724]:
df_by_project = df_by_project.rename_axis(None, axis=1)
df_by_project.head()

Mombasa  Kwale  Kilifi  Tana River  Lamu  Taita-Taveta  \
AEARCTR-0000016        0      0       0           0     0             0   
AEARCTR-0000017        0      0       0           0     0             0   
AEARCTR-0000019        0      0       0           0     0             0   
AEARCTR-0000067        0      0       0           0     0             0   
AEARCTR-0000105        0      0       0           0     0             0   

                 Garissa  Wajir  Mandera  Marsabit  Isiolo  Meru  \
AEARCTR-0000016        0      0        0         0       0     0   
AEARCTR-0000017        0      0        0         0       0     0   
AEARCTR-0000019        0      0        0         0       0     0   
AEARCTR-0000067        0      0        0         0       0     0   
AEARCTR-0000105        0      0        0         0       0     1   

                 Tharaka-Nithi  Embu  Kitui  Machakos  Makueni  Nyandarua  \
AEARCTR-0000016              0     0      0         0        0          0   
AEARCTR-0000017              0     0      0         0        0          0   
AEARCTR-0000019              0     0      0         0        0          0   
AEARCTR-0000067              0     0      0         0        0          0   
AEARCTR-0000105              0     0      0         0        0          0   

                 Nyeri  Kirinyaga  Murang'a  Kiambu  Turkana  West Pokot  \
AEARCTR-0000016      0          0         0       0        0           0   
AEARCTR-0000017      0          0         0       0        0           0   
AEARCTR-0000019      0          0         0       0        0           0   
AEARCTR-0000067      0          0         0       0        0           0   
AEARCTR-0000105      0          0         0       0        0           0   

                 Samburu  Trans Nzoia  Uasin Gishu  Elgeyo-Marakwet  Nandi  \
AEARCTR-0000016        0            0            0                0      0   
AEARCTR-0000017        0            0            0                0      0   
AEARCTR-0000019        0            0            0                0      0   
AEARCTR-0000067        0            0            0                0      0   
AEARCTR-0000105        0            0            0                0      0   

                 Baringo  Laikipia  Nakuru  Narok  Kajiado  Kericho  Bomet  \
AEARCTR-0000016        0         0       0      0        0        0      0   
AEARCTR-0000017        0         0       0      0        0        0      0   
AEARCTR-0000019        0         0       0      0        0        0      0   
AEARCTR-0000067        0         0       0      0        0        0      0   
AEARCTR-0000105        0         0       0      0        0        0      0   

                 Kakamega  Vihiga  Bungoma  Busia  Siaya  Kisumu  Homa Bay  \
AEARCTR-0000016         0       0        0      0      0       0         0   
AEARCTR-0000017         0       0        0      0      1       0         0   
AEARCTR-0000019         0       0        0      0      1       0         0   
AEARCTR-0000067         0       0        1      0      0       0         0   
AEARCTR-0000105         0       0        0      0      0       0         0   

                 Migori  Kisii  Nyamira  Nairobi  
AEARCTR-0000016       0      0        0        1  
AEARCTR-0000017       0      0        0        0  
AEARCTR-0000019       0      0        0        0  
AEARCTR-0000067       0      0        0        0  
AEARCTR-0000105       0      0        0        0

In [725]:
# Transpose project-level dataframe to get county-level dataframe
df_by_county = df_by_project.T
df_by_county

AEARCTR-0000016  AEARCTR-0000017  AEARCTR-0000019  \
Mombasa                        0                0                0   
Kwale                          0                0                0   
Kilifi                         0                0                0   
Tana River                     0                0                0   
Lamu                           0                0                0   
Taita-Taveta                   0                0                0   
Garissa                        0                0                0   
Wajir                          0                0                0   
Mandera                        0                0                0   
Marsabit                       0                0                0   
Isiolo                         0                0                0   
Meru                           0                0                0   
Tharaka-Nithi                  0                0                0   
Embu                           0                0                0   
Kitui                          0                0                0   
Machakos                       0                0                0   
Makueni                        0                0                0   
Nyandarua                      0                0                0   
Nyeri                          0                0                0   
Kirinyaga                      0                0                0   
Murang'a                       0                0                0   
Kiambu                         0                0                0   
Turkana                        0                0                0   
West Pokot                     0                0                0   
Samburu                        0                0                0   
Trans Nzoia                    0                0                0   
Uasin Gishu                    0                0                0   
Elgeyo-Marakwet                0                0                0   
Nandi                          0                0                0   
Baringo                        0                0                0   
Laikipia                       0                0                0   
Nakuru                         0                0                0   
Narok                          0                0                0   
Kajiado                        0                0                0   
Kericho                        0                0                0   
Bomet                          0                0                0   
Kakamega                       0                0                0   
Vihiga                         0                0                0   
Bungoma                        0                0                0   
Busia                          0                0                0   
Siaya                          0                1                1   
Kisumu                         0                0                0   
Homa Bay                       0                0                0   
Migori                         0                0                0   
Kisii                          0                0                0   
Nyamira                        0                0                0   
Nairobi                        1                0                0   

                 AEARCTR-0000067  AEARCTR-0000105  AEARCTR-0000218  \
Mombasa                        0                0                0   
Kwale                          0                0                0   
Kilifi                         0                0                0   
Tana River                     0                0                0   
Lamu                           0                0                0   
Taita-Taveta                   0                0                0   
Garissa                        0                0                0   
Wajir                          0                0                0   
Mandera                   

In [726]:
# Reset index and rename column for both dataframes
df_by_project = df_by_project.reset_index().rename({'index': 'RCT_ID'}, axis=1)
df_by_county = df_by_county.reset_index().rename({'index': 'County'}, axis=1)

In [727]:
# Convert dates to Pandas datetime format
kenya_trials_final[['Start date', 'End date']] = kenya_trials[['Start date', 'End date']].apply(pd.to_datetime)
df_by_project = df_by_project.merge(kenya_trials_final[['RCT_ID', 'Start date', 'End date']], how='left', on='RCT_ID')
df_by_project

RCT_ID  Mombasa  Kwale  Kilifi  Tana River  Lamu  Taita-Taveta  \
0    AEARCTR-0000016        0      0       0           0     0             0   
1    AEARCTR-0000017        0      0       0           0     0             0   
2    AEARCTR-0000019        0      0       0           0     0             0   
3    AEARCTR-0000067        0      0       0           0     0             0   
4    AEARCTR-0000105        0      0       0           0     0             0   
5    AEARCTR-0000218        0      0       0           0     0             0   
6    AEARCTR-0000287        0      0       0           0     0             0   
7    AEARCTR-0000323        0      0       0           0     0             0   
8    AEARCTR-0000350        0      0       0           0     0             0   
9    AEARCTR-0000443        0      0       0           0     0             0   
10   AEARCTR-0000459        0      0       0           0     0             0   
11   AEARCTR-0000486        0      0       0           0     0             0   
12   AEARCTR-0000541        0      0       0           0     0             0   
13   AEARCTR-0000605        0      0       0           0     0             0   
14   AEARCTR-0000627        0      0       0           0     0             0   
15   AEARCTR-0000647        0      0       0           0     0             0   
16   AEARCTR-0000662        0      0       0           0     0             0   
17   AEARCTR-0000669        0      0       0           0     0             0   
18   AEARCTR-0000676        0      0       0           0     0             0   
19   AEARCTR-0000705        0      0       0           0     0             0   
20   AEARCTR-0000740        0      0       0           0     0             0   
21   AEARCTR-0000766        0      0       0           0     0             0   
22   AEARCTR-0000788        0      0       0           0     0             0   
23   AEARCTR-0000790        0      0       0           0     0             0   
24   AEARCTR-0000791        0      0       0           0     0             0   
25   AEARCTR-0000843        0      0       0           0     0             0   
26   AEARCTR-0000844        0      0       0           0     0             0   
27   AEARCTR-0000893        0      0       0           0     0             0   
28   AEARCTR-0000907        0      0       0           0     0             0   
29   AEARCTR-0000912        0      0       0           0     0             0   
30   AEARCTR-0000934        0      0       0           0     0             0   
31   AEARCTR-0000946        0      0       0           0     0             0   
32   AEARCTR-0000962        0      0       0           0     0             0   
33   AEARCTR-0000991        0      0       0           0     0             0   
34   AEARCTR-0000996        0      0       0           0     0             0   
35   AEARCTR-0001002        0      0       0           0     0             0   
36   AEARCTR-0001008        0      0       0           0     0             0   
37   AEARCTR-0001076        0      0       0           0     0             0   
38   AEARCTR-0001167        0      0       0           0     0             0   
39   AEARCTR-0001183        0      0       0           0     0             0   
40   AEARCTR-0001187        0      0       0           0     0             0   
41   AEARCTR-0001197        0      0       0           0     0             0   
42   AEARCTR-0001293        0      0       0           0     0             0   
43   AEARCTR-0001304        0      0       0           0     0             0   
44   AEARCTR-0001358        0      0       0           0     0             0   
45   AEARCTR-0001373        0      0       0           0     0             0   
46   AEARCTR-0001432        0      0       0           0     0             0   
47   AEARCTR-0001457        0      0       0           0     0             0   
48   AEARCTR-0001482        0      0       0           0     0             0   
49   AEARCTR-0

In [728]:
df_by_project.shape

(154, 50)

In [729]:
min(df_by_project['Start date'])

Timestamp('2000-06-01 00:00:00')

In [730]:
max(df_by_project['End date'])

Timestamp('2027-12-31 00:00:00')

- Earliest start date is in 2000 and latest end date is in 2027
- Time period: 2014 to 2022 (because of restrictions on availability of data on development outcomes)
- Define coverage variable: for what portion of the 8-year period did the project run?

In [731]:
# Restrict projects dataset to 2014 to 2022 time period
restricted_project = df_by_project[(df_by_project['Start date'].dt.year >= 2014) & (df_by_project['Start date'].dt.year < 2023)]
restricted_project.head()

RCT_ID  Mombasa  Kwale  Kilifi  Tana River  Lamu  Taita-Taveta  \
7   AEARCTR-0000323        0      0       0           0     0             0   
8   AEARCTR-0000350        0      0       0           0     0             0   
11  AEARCTR-0000486        0      0       0           0     0             0   
12  AEARCTR-0000541        0      0       0           0     0             0   
13  AEARCTR-0000605        0      0       0           0     0             0   

    Garissa  Wajir  Mandera  Marsabit  Isiolo  Meru  Tharaka-Nithi  Embu  \
7         0      0        0         0       0     0              0     0   
8         0      0        0         0       0     0              0     0   
11        0      0        0         0       0     0              0     0   
12        0      0        0         0       0     0              0     0   
13        0      0        0         0       0     0              0     0   

    Kitui  Machakos  Makueni  Nyandarua  Nyeri  Kirinyaga  Murang'a  Kiambu  \
7       0         0        0          0      0          0         0       0   
8       0         0        0          0      0          0         0       0   
11      0         0        0          0      0          0         0       0   
12      0         0        0          0      0          0         0       0   
13      0         0        0          0      0          0         0       0   

    Turkana  West Pokot  Samburu  Trans Nzoia  Uasin Gishu  Elgeyo-Marakwet  \
7         0           0        0            0            0                0   
8         0           0        0            0            0                0   
11        0           0        0            0            0                0   
12        0           0        0            0            0                0   
13        0           0        0            0            0                0   

    Nandi  Baringo  Laikipia  Nakuru  Narok  Kajiado  Kericho  Bomet  \
7       0        0         0       0      0        0        0      0   
8       0        0         0       0      0        0        0      0   
11      0        0         0       0      0        0        0      0   
12      0        0         0       0      0        0        0      0   
13      0        0         0       0      0        0        0      0   

    Kakamega  Vihiga  Bungoma  Busia  Siaya  Kisumu  Homa Bay  Migori  Kisii  \
7          0       0        0      0      0       1         0       0      0   
8          0       0        0      1      0       0         0       0      0   
11         1       1        1      1      0       0         0       0      0   
12         0       0        0      0      1       0         0       0      0   
13         0       0        0      0      0       0         0       0      0   

    Nyamira  Nairobi Start date   End date  
7         0        0 2014-01-27 2014-10-26  
8         0        0 2014-02-07 2020-08-31  
11        0        0 2014-08-25 2015-08-25  
12        0        0 2014-11-10 2016-04-30  
13        0        1 2015-01-28 2015-08-15

- More analysis
- The control group should be counties that **never** received the treatment (as that would bias the estimates)
- The treatment group should be counties where research started after 2014

In [732]:
# Find number of projects
a = pd.melt(df_by_project, id_vars=['RCT_ID', 'Start date', 'End date'], var_name='County', value_name='Number Projects')
a_gr = a.groupby('County').agg({'Number Projects': np.sum})
a_gr

Number Projects
County                          
Baringo                        1
Bomet                          2
Bungoma                       28
Busia                         38
Elgeyo-Marakwet                1
Embu                           2
Garissa                        4
Homa Bay                       6
Isiolo                         3
Kajiado                        1
Kakamega                      29
Kericho                        1
Kiambu                         8
Kilifi                         0
Kirinyaga                      9
Kisii                          5
Kisumu                        10
Kitui                          3
Kwale                          1
Laikipia                       1
Lamu                           0
Machakos                       4
Makueni                        4
Mandera                        3
Marsabit                       2
Meru                           5
Migori                         6
Mombasa                        1
Murang'a                       6
Nairobi                       56
Nakuru                         1
Nandi                          1
Narok                          1
Nyamira                        5
Nyandarua                      6
Nyeri                          6
Samburu                        2
Siaya                         11
Taita-Taveta                   0
Tana River                     0
Tharaka-Nithi                  4
Trans Nzoia                    1
Turkana                        1
Uasin Gishu                    1
Vihiga                        23
Wajir                          4
West Pokot                     1

In [733]:
sum(a_gr['Number Projects'])

308

In [734]:
# Find earliest start date and latest end date 
min_start = []
max_end = []
for county in a_gr.reset_index()['County']:
    subset = a[a['County'] == county]
    if sum(subset['Number Projects']) == 0:
        min_start.append(0)
        max_end.append(0)
    else:
        val_start = min(subset[subset['Number Projects'] > 0]['Start date'].dt.year)
        val_end = max(subset[subset['Number Projects'] > 0]['End date'].dt.year)
        min_start.append(val_start)
        max_end.append(val_end)
        
a_gr['min_start'] = min_start
a_gr['max_end'] = max_end

In [735]:
a_gr

Number Projects  min_start  max_end
County                                              
Baringo                        1       2009     2015
Bomet                          2       2009     2023
Bungoma                       28       2007     2025
Busia                         38       2000     2025
Elgeyo-Marakwet                1       2009     2015
Embu                           2       2023     2024
Garissa                        4       2009     2022
Homa Bay                       6       2013     2024
Isiolo                         3       2023     2024
Kajiado                        1       2009     2015
Kakamega                      29       2003     2025
Kericho                        1       2009     2015
Kiambu                         8       2009     2027
Kilifi                         0          0        0
Kirinyaga                      9       2003     2027
Kisii                          5       2013     2020
Kisumu                        10       2013     2026
Kitui                          3       2016     2024
Kwale                          1       2020     2020
Laikipia                       1       2009     2015
Lamu                           0          0        0
Machakos                       4       2022     2024
Makueni                        4       2016     2024
Mandera                        3       2009     2022
Marsabit                       2       2023     2024
Meru                           5       2013     2024
Migori                         6       2013     2020
Mombasa                        1       2021     2021
Murang'a                       6       2009     2027
Nairobi                       56       2010     2025
Nakuru                         1       2009     2015
Nandi                          1       2009     2015
Narok                          1       2009     2015
Nyamira                        5       2013     2020
Nyandarua                      6       2009     2027
Nyeri                          6       2009     2027
Samburu                        2       2009     2015
Siaya                         11       2011     2021
Taita-Taveta                   0          0        0
Tana River                     0          0        0
Tharaka-Nithi                  4       2017     2026
Trans Nzoia                    1       2009     2015
Turkana                        1       2009     2015
Uasin Gishu                    1       2009     2015
Vihiga                        23       2007     2025
Wajir                          4       2009     2022
West Pokot                     1       2009     2015

In [736]:
# Filter to restrict time period
a_gr_filtered = a_gr[(a_gr['min_start'] == 0) | (a_gr['min_start'] >= 2014)]
a_gr_filtered

Number Projects  min_start  max_end
County                                            
Embu                         2       2023     2024
Isiolo                       3       2023     2024
Kilifi                       0          0        0
Kitui                        3       2016     2024
Kwale                        1       2020     2020
Lamu                         0          0        0
Machakos                     4       2022     2024
Makueni                      4       2016     2024
Marsabit                     2       2023     2024
Mombasa                      1       2021     2021
Taita-Taveta                 0          0        0
Tana River                   0          0        0
Tharaka-Nithi                4       2017     2026

In [737]:
a_gr_filtered.shape

(13, 3)

- Only 13 counties remain: not that much better than province-level analysis

In [738]:
sum(a_gr_filtered['Number Projects'])

24

In [739]:
# Define coverage variable: for what portion of the 7 years did the study run?
restricted_project['Coverage'] = (restricted_project['End date'].dt.year - 2015)/7
restricted_project['Coverage']

7     -0.142857
8      0.714286
11     0.000000
12     0.142857
13     0.000000
14    -0.142857
16     0.142857
17     0.142857
18     0.142857
21     0.000000
22     0.142857
23     0.000000
24     0.000000
25     0.428571
26     0.285714
27    -0.142857
28     0.000000
29     0.142857
32     0.571429
33     0.142857
34     1.285714
36     0.142857
40     0.428571
42     0.428571
45     0.428571
47     0.000000
48     0.285714
49     0.714286
50     0.285714
51     0.142857
52     0.142857
54     0.285714
60     0.000000
62     0.285714
63     0.285714
64     0.428571
65     0.285714
66     0.000000
67     0.285714
68     0.285714
69     0.571429
70     0.142857
71     0.285714
72     0.285714
73     0.285714
74     0.285714
75     0.428571
76     1.142857
77     0.571429
78     0.714286
79     0.285714
80     0.857143
81     1.000000
82     0.428571
83     0.428571
84     0.571429
85     0.571429
87     0.571429
89     0.571429
90     0.428571
91     0.571429
92     1.285714
93     0

In [740]:
# Create dataset at the project-county level
df_county_project = pd.melt(restricted_project, id_vars=['RCT_ID', 'Start date', 'End date', 'Coverage'], var_name='County', value_name='Number Projects')
df_county_project

RCT_ID Start date   End date  Coverage           County  \
0     AEARCTR-0000323 2014-01-27 2014-10-26 -0.142857          Mombasa   
1     AEARCTR-0000350 2014-02-07 2020-08-31  0.714286          Mombasa   
2     AEARCTR-0000486 2014-08-25 2015-08-25  0.000000          Mombasa   
3     AEARCTR-0000541 2014-11-10 2016-04-30  0.142857          Mombasa   
4     AEARCTR-0000605 2015-01-28 2015-08-15  0.000000          Mombasa   
5     AEARCTR-0000627 2014-11-01 2014-12-31 -0.142857          Mombasa   
6     AEARCTR-0000662 2015-05-04 2016-09-15  0.142857          Mombasa   
7     AEARCTR-0000669 2015-04-14 2016-09-15  0.142857          Mombasa   
8     AEARCTR-0000676 2015-04-08 2016-12-31  0.142857          Mombasa   
9     AEARCTR-0000766 2015-04-25 2015-06-15  0.000000          Mombasa   
10    AEARCTR-0000788 2014-09-15 2016-01-01  0.142857          Mombasa   
11    AEARCTR-0000790 2015-06-29 2015-09-01  0.000000          Mombasa   
12    AEARCTR-0000791 2015-02-01 2015-07-01  0.000000          Mombasa   
13    AEARCTR-0000843 2015-09-15 2018-08-31  0.428571          Mombasa   
14    AEARCTR-0000844 2015-09-15 2017-03-22  0.285714          Mombasa   
15    AEARCTR-0000893 2014-05-01 2014-08-01 -0.142857          Mombasa   
16    AEARCTR-0000907 2015-10-08 2015-11-30  0.000000          Mombasa   
17    AEARCTR-0000912 2015-06-11 2016-04-01  0.142857          Mombasa   
18    AEARCTR-0000962 2015-01-13 2019-12-31  0.571429          Mombasa   
19    AEARCTR-0000991 2015-07-01 2016-06-01  0.142857          Mombasa   
20    AEARCTR-0000996 2016-01-11 2024-12-31  1.285714          Mombasa   
21    AEARCTR-0001008 2015-10-01 2016-01-01  0.142857          Mombasa   
22    AEARCTR-0001187 2016-06-01 2018-04-01  0.428571          Mombasa   
23    AEARCTR-0001293 2014-06-01 2018-01-01  0.428571          Mombasa   
24    AEARCTR-0001373 2017-04-03 2018-07-31  0.428571          Mombasa   
25    AEARCTR-0001457 2015-06-01 2015-11-28  0.000000          Mombasa   
26    AEARCTR-0001482 2016-01-01 2017-08-01  0.285714          Mombasa   
27    AEARCTR-0001484 2016-07-04 2020-12-31  0.714286          Mombasa   
28    AEARCTR-0001500 2016-09-19 2017-12-31  0.285714          Mombasa   
29    AEARCTR-0001515 2015-01-01 2016-07-01  0.142857          Mombasa   
30    AEARCTR-0001574 2016-09-14 2016-09-26  0.142857          Mombasa   
31    AEARCTR-0001643 2016-09-05 2017-12-31  0.285714          Mombasa   
32    AEARCTR-0001848 2015-03-13 2015-08-10  0.000000          Mombasa   
33    AEARCTR-0001902 2016-08-25 2017-05-15  0.285714          Mombasa   
34    AEARCTR-0001997 2016-11-07 2017-01-29  0.285714          Mombasa   
35    AEARCTR-0002015 2016-06-01 2018-03-31  0.428571          Mombasa   
36    AEARCTR-0002019 2016-08-01 2017-12-31  0.285714          Mombasa   
37    AEARCTR-0002026 2015-03-02 2015-05-08  0.000000          Mombasa   
38    AEARCTR-0002063 2014-06-01 2017-12-31  0.285714          Mombasa   
39    AEARCTR-0002071 2016-11-16 2017-03-01  0.285714          Mombasa   
40    AEARCTR-0002133 2015-03-01 2019-08-05  0.571429          Mombasa   
41    AEARCTR-0002188 2015-08-01 2016-11-30  0.142857          Mombasa   
42    AEARCTR-0002313 2015-06-01 2017-10-30  0.285714          Mombasa   
43    AEARCTR-0002370 2014-01-01 2017-07-30  0.285714          Mombasa   
44    AEARCTR-0002375 2017-07-12 2017-08-05  0.285714          Mombasa   
45    AEARCTR-0002401 2017-07-03 2017-12-31  0.285714          Mombasa   
46    AEARCTR-0002448 2017-09-25 2018-09-25  0.428571          Mombasa   
47    AEARCTR-0002484 2017-10-01 2023-12-31  1.142857          Mombasa   
48    AEARCTR-0002579 2016-05-01 2019-06-30  0.571429          Mombasa   
49    AEARCTR-0002692 2018-05-28 2020-02-01  0.714286          Mombasa   
50    AEARCTR-0002741 2017-02-15 2017-12-13  0.285714          Mombasa   
51    AEARCTR-0002850 2017-10-01 2021-02-01  0.857143          Mombasa   
52    AEARCTR-0002913 2017-08-03 2022-05-31  1.000000          Mombasa   
53    AEARCTR-00029

In [741]:
df_county_project.shape

(5029, 6)

In [742]:
# Find total number of projects for each county
grouped_data = df_county_project.groupby('County').agg({'Number Projects': np.sum})
grouped_data

Number Projects
County                          
Baringo                        0
Bomet                          0
Bungoma                       18
Busia                         21
Elgeyo-Marakwet                0
Embu                           0
Garissa                        2
Homa Bay                       5
Isiolo                         0
Kajiado                        0
Kakamega                      17
Kericho                        0
Kiambu                         4
Kilifi                         0
Kirinyaga                      4
Kisii                          4
Kisumu                         8
Kitui                          1
Kwale                          1
Laikipia                       0
Lamu                           0
Machakos                       2
Makueni                        2
Mandera                        2
Marsabit                       0
Meru                           2
Migori                         5
Mombasa                        1
Murang'a                       2
Nairobi                       46
Nakuru                         0
Nandi                          0
Narok                          0
Nyamira                        4
Nyandarua                      2
Nyeri                          2
Samburu                        1
Siaya                          8
Taita-Taveta                   0
Tana River                     0
Tharaka-Nithi                  1
Trans Nzoia                    0
Turkana                        0
Uasin Gishu                    0
Vihiga                        15
Wajir                          3
West Pokot                     0

In [743]:
# Compute coverage by county
county_cov = []
for county in grouped_data.reset_index()['County']:
    subset = df_county_project[df_county_project['County'] == county]
    if sum(subset['Number Projects']) == 0:
        county_cov.append(0)
    else:
        cov = np.mean(subset[subset['Number Projects'] > 0]['Coverage'])
        county_cov.append(cov)

In [744]:
# Transpose project-level dataframe to get county-level dataframe
restricted_county = restricted_project.iloc[:, :48].set_index('RCT_ID').T.reset_index().rename_axis(None, axis=1).rename({'index': 'County'}, axis=1)
restricted_county.sort_values(by='County', inplace=True)
restricted_county['Coverage'] = county_cov
restricted_county

County  AEARCTR-0000323  AEARCTR-0000350  AEARCTR-0000486  \
29          Baringo                0                0                0   
35            Bomet                0                0                0   
38          Bungoma                0                0                1   
39            Busia                0                1                1   
27  Elgeyo-Marakwet                0                0                0   
13             Embu                0                0                0   
6           Garissa                0                0                0   
42         Homa Bay                0                0                0   
10           Isiolo                0                0                0   
33          Kajiado                0                0                0   
36         Kakamega                0                0                1   
34          Kericho                0                0                0   
21           Kiambu                0                0                0   
2            Kilifi                0                0                0   
19        Kirinyaga                0                0                0   
44            Kisii                0                0                0   
41           Kisumu                1                0                0   
14            Kitui                0                0                0   
1             Kwale                0                0                0   
30         Laikipia                0                0                0   
4              Lamu                0                0                0   
15         Machakos                0                0                0   
16          Makueni                0                0                0   
8           Mandera                0                0                0   
9          Marsabit                0                0                0   
11             Meru                0                0                0   
43           Migori                0                0                0   
0           Mombasa                0                0                0   
20         Murang'a                0                0                0   
46          Nairobi                0                0                0   
31           Nakuru                0                0                0   
28            Nandi                0                0                0   
32            Narok                0                0                0   
45          Nyamira                0                0                0   
17        Nyandarua                0                0                0   
18            Nyeri                0                0                0   
24          Samburu                0                0                0   
40            Siaya                0                0                0   
5      Taita-Taveta                0                0                0   
3        Tana River                0                0                0   
12    Tharaka-Nithi                0                0                0   
25      Trans Nzoia                0                0                0   
22          Turkana                0                0                0   
26      Uasin Gishu                0                0                0   
37           Vihiga                0                0                1   
7             Wajir                0                0                0   
23       West Pokot                0                0                0   

    AEARCTR-0000541  AEARCTR-0000605  AEARCTR-0000627  AEARCTR-0000662  \
29                0                0                0                0   
35                0                0                0                0   
38                0                0                0                0   
39                0                0                0                0   
27                0                0                0                0   
13              

In [745]:
restricted_county.shape

(47, 109)

In [746]:
# Merge with county-level data
restricted_county = restricted_county.merge(grouped_data.reset_index(), on='County', how='left')
restricted_county

County  AEARCTR-0000323  AEARCTR-0000350  AEARCTR-0000486  \
0           Baringo                0                0                0   
1             Bomet                0                0                0   
2           Bungoma                0                0                1   
3             Busia                0                1                1   
4   Elgeyo-Marakwet                0                0                0   
5              Embu                0                0                0   
6           Garissa                0                0                0   
7          Homa Bay                0                0                0   
8            Isiolo                0                0                0   
9           Kajiado                0                0                0   
10         Kakamega                0                0                1   
11          Kericho                0                0                0   
12           Kiambu                0                0                0   
13           Kilifi                0                0                0   
14        Kirinyaga                0                0                0   
15            Kisii                0                0                0   
16           Kisumu                1                0                0   
17            Kitui                0                0                0   
18            Kwale                0                0                0   
19         Laikipia                0                0                0   
20             Lamu                0                0                0   
21         Machakos                0                0                0   
22          Makueni                0                0                0   
23          Mandera                0                0                0   
24         Marsabit                0                0                0   
25             Meru                0                0                0   
26           Migori                0                0                0   
27          Mombasa                0                0                0   
28         Murang'a                0                0                0   
29          Nairobi                0                0                0   
30           Nakuru                0                0                0   
31            Nandi                0                0                0   
32            Narok                0                0                0   
33          Nyamira                0                0                0   
34        Nyandarua                0                0                0   
35            Nyeri                0                0                0   
36          Samburu                0                0                0   
37            Siaya                0                0                0   
38     Taita-Taveta                0                0                0   
39       Tana River                0                0                0   
40    Tharaka-Nithi                0                0                0   
41      Trans Nzoia                0                0                0   
42          Turkana                0                0                0   
43      Uasin Gishu                0                0                0   
44           Vihiga                0                0                1   
45            Wajir                0                0                0   
46       West Pokot                0                0                0   

    AEARCTR-0000541  AEARCTR-0000605  AEARCTR-0000627  AEARCTR-0000662  \
0                 0                0                0                0   
1                 0                0                0                0   
2                 0                0                0                0   
3                 0                0                0                0   
4                 0                0                0                0   
5               

## Data on Outcome Variables

- Spatial data from DHS in 2014 and 2022
- These are the only years for which I found find county-level data
- Kenyan counties were established in 2010 so cannot find county-level data before then

In [747]:
# Define function for reading Shapefiles
def read_shapefile(sf_shape):
    """
    Read a shapefile into a Pandas dataframe with a 'coords' 
    column holding the geometry information. This uses the pyshp
    package
    """

    fields = [x[0] for x in sf_shape.fields][1:]
    records = [y[:] for y in sf_shape.records()]
    #records = sf_shape.records()
    shps = [s.points for s in sf_shape.shapes()]
    df = pd.DataFrame(columns=fields, data=records)
    df = df.assign(coords=shps)
    return df

In [748]:
# Read 2014 data
sh_educ_2014 = shapefile.Reader('sdr_subnational_data_dhs_2014_lvl_2.shp')
df_educ_2014 = read_shapefile(sh_educ_2014).rename({'DHSREGEN': 'County'}, axis=1)
df_educ_2014.head()

ISO FIPS DHSCC SVYTYPE  SVYYEAR CNTRYNAMEE CNTRYNAMEF CNTRYNAMES  \
0  KE   KE    KE     DHS   2014.0      Kenya                         
1  KE   KE    KE     DHS   2014.0      Kenya                         
2  KE   KE    KE     DHS   2014.0      Kenya                         
3  KE   KE    KE     DHS   2014.0      Kenya                         
4  KE   KE    KE     DHS   2014.0      Kenya                         

            County DHSREGFR DHSREGSP  SVYID           REG_ID Svy_Map  \
0          Baringo                    451.0  KEDHS2014416058     yes   
1            Bomet                    451.0  KEDHS2014416064     yes   
2          Bungoma                    451.0  KEDHS2014416073     yes   
3            Busia                    451.0  KEDHS2014416074     yes   
4  Elgeyo Marakwet                    451.0  KEDHS2014416056     yes   

  MULTLEVEL  LEVELRNK    REGVAR  REGCODE          REGNAME OTHREGVAR  OTHREGCO  \
0       yes       2.0  shcounty     58.0          baringo     hv024       5.0   
1       yes       2.0  shcounty     64.0            bomet     hv024       5.0   
2       yes       2.0  shcounty     73.0          bungoma     hv024       7.0   
3       yes       2.0  shcounty     74.0            busia     hv024       7.0   
4       yes       2.0  shcounty     56.0  elgeyo marakwet     hv024       5.0   

      OTHREGNA LEVELCO   LEVELNA REPALLIND REGNOTES  \
0  rift valley  Admin1  Counties        no            
1  rift valley  Admin1  Counties        no            
2      western  Admin1  Counties        no            
3      western  Admin1  Counties        no            
4  rift valley  Admin1  Counties        no            

                                            SVYNOTES  EDGARPWFEM  EDGARPMMAL  \
0  Survey is representative at two levels: 47 reg...      9999.0      9999.0   
1  Survey is representative at two levels: 47 reg...      9999.0      9999.0   
2  Survey is representative at two levels: 47 reg...      9999.0      9999.0   
3  Survey is representative at two levels: 47 reg...      9999.0      9999.0   
4  Survey is representative at two levels: 47 reg...      9999.0      9999.0   

   EDGARPBBTH  EDGARPBGPI  EDGARSWFEM  EDGARSMMAL  EDGARSBBTH  EDGARSBGPI  \
0      9999.0      9999.0      9999.0      9999.0      9999.0      9999.0   
1      9999.0      9999.0      9999.0      9999.0      9999.0      9999.0   
2      9999.0      9999.0      9999.0      9999.0      9999.0      9999.0   
3      9999.0      9999.0      9999.0      9999.0      9999.0      9999.0   
4      9999.0      9999.0      9999.0      9999.0      9999.0      9999.0   

   EDEDUCWNED  EDEDUCWSPR  EDEDUCWCPR  EDEDUCWSSC  EDEDUCWCSC  EDEDUCWHGH  \
0         9.3        30.0        24.5        15.0        12.1         9.0   
1         0.4        39.8        25.7        14.3        11.5         8.2   
2         0.9        41.2        19.8        20.7        10.3         7.2   
3         6.6        51.6        16.1        14.3         6.0         5.2   
4         1.2        27.7        28.6        14.4        15.0        13.0   

   EDEDUCWDKM  EDEDUCWTOT  EDEDUCWPRI  EDEDUCWSEH  EDEDUCWMYR  EDEDUCWNUM  \
0      9999.0       100.0        54.5        36.1         7.4       335.0   
1      9999.0       100.0        65.5        34.0         7.3       687.0   
2      9999.0       100.0        61.0        38.1         7.3      1203.0   
3      9999.0       100.0        67.7        25.6         6.5       546.0   
4      9999.0       100.0        56.3        42.5         7.7       250.0   

   EDEDUCWUNW  EDEDUCMNED  EDEDUCMSPR  EDEDUCMCPR  EDEDUCMSSC  EDEDUCMCSC  \
0       598.0         5.9        33.3        16.7        15.3        20.1   
1       708.0         0.0        33.1        27.2        14.4        18.1   
2       805.0         0.4        45.2        16.9        17.9        11.5   
3       676.0         1.1        45.7        16.9        18.1        12.4   
4       630.0         0.2        24.4        26.6        13.3        21.4  

In [749]:
# Read 2022 data
sh_educ_2022 = shapefile.Reader('sdr_subnational_data_dhs_2022.shp')
df_educ_2022 = read_shapefile(sh_educ_2022).rename({'DHSREGEN': 'County'}, axis=1)
df_educ_2022.head()

ISO FIPS DHSCC SVYTYPE  SVYYEAR CNTRYNAMEE CNTRYNAMEF CNTRYNAMES  \
0  KE   KE    KE     DHS   2022.0      Kenya                         
1  KE   KE    KE     DHS   2022.0      Kenya                         
2  KE   KE    KE     DHS   2022.0      Kenya                         
3  KE   KE    KE     DHS   2022.0      Kenya                         
4  KE   KE    KE     DHS   2022.0      Kenya                         

            County DHSREGFR DHSREGSP  SVYID           REG_ID Svy_Map  \
0          Baringo                    566.0  KEDHS2022416058     yes   
1            Bomet                    566.0  KEDHS2022416064     yes   
2          Bungoma                    566.0  KEDHS2022416073     yes   
3            Busia                    566.0  KEDHS2022416074     yes   
4  Elgeyo-Marakwet                    566.0  KEDHS2022416056     yes   

  MULTLEVEL  LEVELRNK REGVAR  REGCODE          REGNAME OTHREGVAR  OTHREGCO  \
0        no       1.0  hv024     30.0          Baringo      NULL    9999.0   
1        no       1.0  hv024     36.0            Bomet      NULL    9999.0   
2        no       1.0  hv024     39.0          Bungoma      NULL    9999.0   
3        no       1.0  hv024     40.0            Busia      NULL    9999.0   
4        no       1.0  hv024     28.0  Elgeyo-Marakwet      NULL    9999.0   

  OTHREGNA LEVELCO   LEVELNA REPALLIND REGNOTES  \
0     NULL  Admin1  Counties        no            
1     NULL  Admin1  Counties        no            
2     NULL  Admin1  Counties        no            
3     NULL  Admin1  Counties        no            
4     NULL  Admin1  Counties        no            

                                            SVYNOTES  EDGARPWFEM  EDGARPMMAL  \
0  Survey is representative at one level: 47 regi...       113.3       100.4   
1  Survey is representative at one level: 47 regi...       116.8       125.3   
2  Survey is representative at one level: 47 regi...       114.5       116.1   
3  Survey is representative at one level: 47 regi...       111.5       124.0   
4  Survey is representative at one level: 47 regi...       108.8       112.4   

   EDGARPBBTH  EDGARPBGPI  EDGARSWFEM  EDGARSMMAL  EDGARSBBTH  EDGARSBGPI  \
0       106.2        1.13        66.6        84.5        75.8        0.79   
1       121.2        0.93        87.7        90.7        89.2        0.97   
2       115.3        0.99        78.5        81.6        80.0        0.96   
3       117.9        0.90        89.3        74.9        81.1        1.19   
4       110.7        0.97        98.5        90.8        93.8        1.08   

   EDEDUCWNED  EDEDUCWSPR  EDEDUCWCPR  EDEDUCWSSC  EDEDUCWCSC  EDEDUCWHGH  \
0         5.9        19.7        20.3        17.1        21.2        15.8   
1         0.3        25.4        23.0        24.0        15.5        11.8   
2         0.8        23.7        17.8        26.4        15.2        16.0   
3         3.3        32.6        18.5        24.7        12.4         8.5   
4         0.0        16.2        21.8        17.6        25.0        19.4   

   EDEDUCWDKM  EDEDUCWTOT  EDEDUCWPRI  EDEDUCWSEH  EDEDUCWMYR  EDEDUCWNUM  \
0      9999.0       100.0        40.0        54.1         7.7       378.0   
1      9999.0       100.0        48.4        51.3         7.5       650.0   
2      9999.0       100.0        41.5        57.6         7.6      1138.0   
3      9999.0       100.0        51.1        45.6         7.2       622.0   
4      9999.0       100.0        38.0        62.0         7.9       228.0   

   EDEDUCWUNW  EDEDUCMNED  EDEDUCMSPR  EDEDUCMCPR  EDEDUCMSSC  EDEDUCMCSC  \
0       687.0         3.1        20.3        20.1        18.6        21.0   
1       778.0         0.4        22.8        22.1        22.6        16.4   
2       841.0         0.3        26.0        15.7        24.5        15.5   
3       768.0         0.7        35.9        16.1        22.2        12.2   
4       591.0         0.0        15.5        20.8        26.3        20.7   

   EDEDUCMHGH  EDEDUCMDKM  EDEDUCMTOT  

In [750]:
df_educ_2022 = df_educ_2022.merge(counties, on='County', how='left')
mmm = df_educ_2022.groupby('Province').first().reset_index()

In [751]:
mmm

Province ISO FIPS DHSCC SVYTYPE  SVYYEAR CNTRYNAMEE CNTRYNAMEF  \
0      Central  KE   KE    KE     DHS   2022.0      Kenya              
1        Coast  KE   KE    KE     DHS   2022.0      Kenya              
2      Eastern  KE   KE    KE     DHS   2022.0      Kenya              
3      Nairobi  KE   KE    KE     DHS   2022.0      Kenya              
4     Northern  KE   KE    KE     DHS   2022.0      Kenya              
5       Nyanza  KE   KE    KE     DHS   2022.0      Kenya              
6  Rift Valley  KE   KE    KE     DHS   2022.0      Kenya              
7      Western  KE   KE    KE     DHS   2022.0      Kenya              

  CNTRYNAMES    County DHSREGFR DHSREGSP  SVYID           REG_ID Svy_Map  \
0               Kiambu                    566.0  KEDHS2022416045     yes   
1               Kilifi                    566.0  KEDHS2022416013     yes   
2                 Embu                    566.0  KEDHS2022416035     yes   
3              Nairobi                    566.0  KEDHS2022416001     yes   
4              Garissa                    566.0  KEDHS2022416021     yes   
5             Homa Bay                    566.0  KEDHS2022416083     yes   
6              Baringo                    566.0  KEDHS2022416058     yes   
7              Bungoma                    566.0  KEDHS2022416073     yes   

  MULTLEVEL  LEVELRNK REGVAR  REGCODE   REGNAME OTHREGVAR  OTHREGCO OTHREGNA  \
0        no       1.0  hv024     22.0    Kiambu      NULL    9999.0     NULL   
1        no       1.0  hv024      3.0    Kilifi      NULL    9999.0     NULL   
2        no       1.0  hv024     14.0      Embu      NULL    9999.0     NULL   
3        no       1.0  hv024     47.0   Nairobi      NULL    9999.0     NULL   
4        no       1.0  hv024      7.0   Garissa      NULL    9999.0     NULL   
5        no       1.0  hv024     43.0  Homa Bay      NULL    9999.0     NULL   
6        no       1.0  hv024     30.0   Baringo      NULL    9999.0     NULL   
7        no       1.0  hv024     39.0   Bungoma      NULL    9999.0     NULL   

  LEVELCO   LEVELNA REPALLIND REGNOTES  \
0  Admin1  Counties        no            
1  Admin1  Counties        no            
2  Admin1  Counties        no            
3  Admin1  Counties        no            
4  Admin1  Counties        no            
5  Admin1  Counties        no            
6  Admin1  Counties        no            
7  Admin1  Counties        no            

                                            SVYNOTES  EDGARPWFEM  EDGARPMMAL  \
0  Survey is representative at one level: 47 regi...       104.2       106.1   
1  Survey is representative at one level: 47 regi...       121.5       122.0   
2  Survey is representative at one level: 47 regi...       105.1       112.5   
3  Survey is representative at one level: 47 regi...       102.7       100.1   
4  Survey is representative at one level: 47 regi...        66.0        62.6   
5  Survey is representative at one level: 47 regi...       100.7       111.5   
6  Survey is representative at one level: 47 regi...       113.3       100.4   
7  Survey is representative at one level: 47 regi...       114.5       116.1   

   EDGARPBBTH  EDGARPBGPI  EDGARSWFEM  EDGARSMMAL  EDGARSBBTH  EDGARSBGPI  \
0       105.1        0.98       106.2        92.4        98.7        1.15   
1       121.8        1.00        46.6        69.0        58.3        0.68   
2       108.8        0.93       127.3        85.8       101.7        1.48   
3       101.5        1.03       112.3        98.7       105.5        1.14   
4        64.1        1.05        34.7        51.8        42.4        0.67   
5       106.0        0.90        94.1        76.9        84.7        1.22   
6       106.2        1.13        66.6        84.5        75.8        0.79   
7       115.3        0.99        78.5        81.6        80.0        0.96   

   EDEDUCWNED  EDEDUCWSPR  EDEDUCWCPR  EDEDUCWSSC  EDEDUCWCSC  EDEDUCWHGH  \
0         0.5         8.8        14.9        18.9        25.6        31.4   
1  

In [752]:
# Add column to indicate treatment status
restricted_county['treated_num'] = [0 if restricted_county['Number Projects'].iloc[i] == 0 else 1 for i in range(len(restricted_county))]
restricted_county['treated_cov'] = [0 if restricted_county['Coverage'].iloc[i] == 0 else 1 for i in range(len(restricted_county))]

In [753]:
# Discretize treatment variables

# Discretize number of projects into 3 categories: low, medium, high
num_low, num_med, num_high = [], [], []
for i in restricted_county['Number Projects']:
    if i == 0:
        num_low.append(1)
        num_med.append(0)
        num_high.append(0)
    elif (i > 0 and i < 20):
        num_low.append(0)
        num_med.append(1)
        num_high.append(0)
    elif (i >= 20):
        num_low.append(0)
        num_med.append(0)
        num_high.append(1)
        
restricted_county['num_low'] = num_low
restricted_county['num_med'] = num_med
restricted_county['num_high'] = num_high

In [754]:
# Discretize coverage into 3 categories: low, medium, high
cov_low, cov_med, cov_high = [], [], []
for i in restricted_county['Coverage']:
    if i == 0:
        cov_low.append(1)
        cov_med.append(0)
        cov_high.append(0)
    elif (i > 0 and i < .50):
        cov_low.append(0)
        cov_med.append(1)
        cov_high.append(0)
    elif (i >= .50):
        cov_low.append(0)
        cov_med.append(0)
        cov_high.append(1)
        
restricted_county['cov_low'] = cov_low
restricted_county['cov_med'] = cov_med
restricted_county['cov_high'] = cov_high

In [755]:
# Merge data on trials with data on outcome variables
restricted_county_outcome = restricted_county.merge(df_educ_2014, on='County', how='left').merge(mmm, on='County', how='left')
restricted_county_outcome

County  AEARCTR-0000323  AEARCTR-0000350  AEARCTR-0000486  \
0           Baringo                0                0                0   
1             Bomet                0                0                0   
2           Bungoma                0                0                1   
3             Busia                0                1                1   
4   Elgeyo-Marakwet                0                0                0   
5              Embu                0                0                0   
6           Garissa                0                0                0   
7          Homa Bay                0                0                0   
8            Isiolo                0                0                0   
9           Kajiado                0                0                0   
10         Kakamega                0                0                1   
11          Kericho                0                0                0   
12           Kiambu                0                0                0   
13           Kilifi                0                0                0   
14        Kirinyaga                0                0                0   
15            Kisii                0                0                0   
16           Kisumu                1                0                0   
17            Kitui                0                0                0   
18            Kwale                0                0                0   
19         Laikipia                0                0                0   
20             Lamu                0                0                0   
21         Machakos                0                0                0   
22          Makueni                0                0                0   
23          Mandera                0                0                0   
24         Marsabit                0                0                0   
25             Meru                0                0                0   
26           Migori                0                0                0   
27          Mombasa                0                0                0   
28         Murang'a                0                0                0   
29          Nairobi                0                0                0   
30           Nakuru                0                0                0   
31            Nandi                0                0                0   
32            Narok                0                0                0   
33          Nyamira                0                0                0   
34        Nyandarua                0                0                0   
35            Nyeri                0                0                0   
36          Samburu                0                0                0   
37            Siaya                0                0                0   
38     Taita-Taveta                0                0                0   
39       Tana River                0                0                0   
40    Tharaka-Nithi                0                0                0   
41      Trans Nzoia                0                0                0   
42          Turkana                0                0                0   
43      Uasin Gishu                0                0                0   
44           Vihiga                0                0                1   
45            Wajir                0                0                0   
46       West Pokot                0                0                0   

    AEARCTR-0000541  AEARCTR-0000605  AEARCTR-0000627  AEARCTR-0000662  \
0                 0                0                0                0   
1                 0                0                0                0   
2                 0                0                0                0   
3                 0                0                0                0   
4                 0                0                0                0   
5               

In [756]:
a_gr_outcome = a_gr_filtered.merge(df_educ_2014, on='County', how='left').merge(df_educ_2022, on='County', how='left')
a_gr_outcome

County  Number Projects  min_start  max_end ISO_x FIPS_x DHSCC_x  \
0            Embu                2       2023     2024    KE     KE      KE   
1          Isiolo                3       2023     2024    KE     KE      KE   
2          Kilifi                0          0        0    KE     KE      KE   
3           Kitui                3       2016     2024    KE     KE      KE   
4           Kwale                1       2020     2020    KE     KE      KE   
5            Lamu                0          0        0    KE     KE      KE   
6        Machakos                4       2022     2024    KE     KE      KE   
7         Makueni                4       2016     2024    KE     KE      KE   
8        Marsabit                2       2023     2024    KE     KE      KE   
9         Mombasa                1       2021     2021    KE     KE      KE   
10   Taita-Taveta                0          0        0   NaN    NaN     NaN   
11     Tana River                0          0        0    KE     KE      KE   
12  Tharaka-Nithi                4       2017     2026    KE     KE      KE   

   SVYTYPE_x  SVYYEAR_x CNTRYNAMEE_x CNTRYNAMEF_x CNTRYNAMES_x DHSREGFR_x  \
0        DHS     2014.0        Kenya                                        
1        DHS     2014.0        Kenya                                        
2        DHS     2014.0        Kenya                                        
3        DHS     2014.0        Kenya                                        
4        DHS     2014.0        Kenya                                        
5        DHS     2014.0        Kenya                                        
6        DHS     2014.0        Kenya                                        
7        DHS     2014.0        Kenya                                        
8        DHS     2014.0        Kenya                                        
9        DHS     2014.0        Kenya                                        
10       NaN        NaN          NaN          NaN          NaN        NaN   
11       DHS     2014.0        Kenya                                        
12       DHS     2014.0        Kenya                                        

   DHSREGSP_x  SVYID_x         REG_ID_x Svy_Map_x MULTLEVEL_x  LEVELRNK_x  \
0                451.0  KEDHS2014416035       yes         yes         2.0   
1                451.0  KEDHS2014416032       yes         yes         2.0   
2                451.0  KEDHS2014416013       yes         yes         2.0   
3                451.0  KEDHS2014416036       yes         yes         2.0   
4                451.0  KEDHS2014416012       yes         yes         2.0   
5                451.0  KEDHS2014416015       yes         yes         2.0   
6                451.0  KEDHS2014416037       yes         yes         2.0   
7                451.0  KEDHS2014416038       yes         yes         2.0   
8                451.0  KEDHS2014416031       yes         yes         2.0   
9                451.0  KEDHS2014416011       yes         yes         2.0   
10        NaN      NaN              NaN       NaN         NaN         NaN   
11               451.0  KEDHS2014416014       yes         yes         2.0   
12               451.0  KEDHS2014416034       yes         yes         2.0   

    REGVAR_x  REGCODE_x      REGNAME_x OTHREGVAR_x  OTHREGCO_x OTHREGNA_x  \
0   shcounty       35.0           embu       hv024         3.0    eastern   
1   shcounty       32.0         isiolo       hv024         3.0    eastern   
2   shcounty       13.0         kilifi       hv024         1.0      coast   
3   shcounty       36.0          kitui       hv024         3.0    eastern   
4   shcounty       12.0          kwale       hv024         1.0      coast   
5   shcounty       15.0           lamu       hv024         1.0      coast   
6   shcounty       37.0       machakos       hv024         3.0    eastern   
7   shcounty       38.0        makueni       hv024         3.0    eastern   
8   shcounty       31.0       marsabit       hv024   

In [757]:
a_gr_outcome['treated'] = [0 if a_gr_filtered['Number Projects'].iloc[i] == 0 else 1 for i in range(len(a_gr_filtered))]
a_gr_outcome

County  Number Projects  min_start  max_end ISO_x FIPS_x DHSCC_x  \
0            Embu                2       2023     2024    KE     KE      KE   
1          Isiolo                3       2023     2024    KE     KE      KE   
2          Kilifi                0          0        0    KE     KE      KE   
3           Kitui                3       2016     2024    KE     KE      KE   
4           Kwale                1       2020     2020    KE     KE      KE   
5            Lamu                0          0        0    KE     KE      KE   
6        Machakos                4       2022     2024    KE     KE      KE   
7         Makueni                4       2016     2024    KE     KE      KE   
8        Marsabit                2       2023     2024    KE     KE      KE   
9         Mombasa                1       2021     2021    KE     KE      KE   
10   Taita-Taveta                0          0        0   NaN    NaN     NaN   
11     Tana River                0          0        0    KE     KE      KE   
12  Tharaka-Nithi                4       2017     2026    KE     KE      KE   

   SVYTYPE_x  SVYYEAR_x CNTRYNAMEE_x CNTRYNAMEF_x CNTRYNAMES_x DHSREGFR_x  \
0        DHS     2014.0        Kenya                                        
1        DHS     2014.0        Kenya                                        
2        DHS     2014.0        Kenya                                        
3        DHS     2014.0        Kenya                                        
4        DHS     2014.0        Kenya                                        
5        DHS     2014.0        Kenya                                        
6        DHS     2014.0        Kenya                                        
7        DHS     2014.0        Kenya                                        
8        DHS     2014.0        Kenya                                        
9        DHS     2014.0        Kenya                                        
10       NaN        NaN          NaN          NaN          NaN        NaN   
11       DHS     2014.0        Kenya                                        
12       DHS     2014.0        Kenya                                        

   DHSREGSP_x  SVYID_x         REG_ID_x Svy_Map_x MULTLEVEL_x  LEVELRNK_x  \
0                451.0  KEDHS2014416035       yes         yes         2.0   
1                451.0  KEDHS2014416032       yes         yes         2.0   
2                451.0  KEDHS2014416013       yes         yes         2.0   
3                451.0  KEDHS2014416036       yes         yes         2.0   
4                451.0  KEDHS2014416012       yes         yes         2.0   
5                451.0  KEDHS2014416015       yes         yes         2.0   
6                451.0  KEDHS2014416037       yes         yes         2.0   
7                451.0  KEDHS2014416038       yes         yes         2.0   
8                451.0  KEDHS2014416031       yes         yes         2.0   
9                451.0  KEDHS2014416011       yes         yes         2.0   
10        NaN      NaN              NaN       NaN         NaN         NaN   
11               451.0  KEDHS2014416014       yes         yes         2.0   
12               451.0  KEDHS2014416034       yes         yes         2.0   

    REGVAR_x  REGCODE_x      REGNAME_x OTHREGVAR_x  OTHREGCO_x OTHREGNA_x  \
0   shcounty       35.0           embu       hv024         3.0    eastern   
1   shcounty       32.0         isiolo       hv024         3.0    eastern   
2   shcounty       13.0         kilifi       hv024         1.0      coast   
3   shcounty       36.0          kitui       hv024         3.0    eastern   
4   shcounty       12.0          kwale       hv024         1.0      coast   
5   shcounty       15.0           lamu       hv024         1.0      coast   
6   shcounty       37.0       machakos       hv024         3.0    eastern   
7   shcounty       38.0        makueni       hv024         3.0    eastern   
8   shcounty       31.0       marsabit       hv024   

# Descriptive Analysis

## Summary Statistics

## Data Visualization

# Econometric Analysis

## Differences-in-Differences Regression

In [758]:
# Define function for creating the regression table
def create_reg_table(var, new_var, x1, x2=None):
    # Pre-treatment data
    if (x2 != None):
        cols = [var + '_x', x1, x2]
    else:
        cols = [var + '_x', x1]
    df_before = restricted_county_outcome[cols]
    df_before['t'] = 0
    df_before.rename({var + '_x': new_var}, axis=1, inplace=True)

    # Post-treatment data
    if (x2 != None):
        cols = [var + '_y', x1, x2]
    else:
        cols = [var + '_y', x1]
    df_after = restricted_county_outcome[cols]
    df_after['t'] = 1
    df_after.rename({var + '_y': new_var}, axis=1, inplace=True)

    # Merged data
    df_reg = pd.concat([df_before, df_after])
    df_reg.dropna(inplace=True)
    
    return df_reg

### 1. Education

#### 1.1. Percentage of men with some primary education

In [759]:
# Create regression tables for each of the 2 independent variables
var1 = 'EDEDUCWSPR'
df_reg_educ_num_1 = create_reg_table(var1, 'educ', 'treated_num')
df_reg_educ_cov_1 = create_reg_table(var1, 'educ', 'treated_cov')

# Run regression
mod_educ_num_1 = ols('educ ~ treated_num + t + treated_num*t', data=df_reg_educ_num_1).fit(cov_type='HC1')
mod_educ_cov_1 = ols('educ ~ treated_cov + t + treated_cov*t', data=df_reg_educ_cov_1).fit(cov_type='HC1')

In [760]:
print(mod_educ_num_1.summary())

                            OLS Regression Results                            
Dep. Variable:                   educ   R-squared:                       0.104
Model:                            OLS   Adj. R-squared:                  0.048
Method:                 Least Squares   F-statistic:                     3.751
Date:                Thu, 25 Apr 2024   Prob (F-statistic):             0.0168
Time:                        22:10:15   Log-Likelihood:                -197.88
No. Observations:                  52   AIC:                             403.8
Df Residuals:                      48   BIC:                             411.6
Df Model:                           3                                         
Covariance Type:                  HC1                                         
                    coef    std err          z      P>|z|      [0.025      0.975]
---------------------------------------------------------------------------------
Intercept        28.7588      2.275     12.642

In [761]:
m1 = ols('educ ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table(var1, 'educ', 'num_med', 'num_high')).fit(cov_type='HC1')
print(m1.summary())

                            OLS Regression Results                            
Dep. Variable:                   educ   R-squared:                       0.124
Model:                            OLS   Adj. R-squared:                  0.028
Method:                 Least Squares   F-statistic:                     34.62
Date:                Thu, 25 Apr 2024   Prob (F-statistic):           1.64e-14
Time:                        22:10:15   Log-Likelihood:                -197.29
No. Observations:                  52   AIC:                             406.6
Df Residuals:                      46   BIC:                             418.3
Df Model:                           5                                         
Covariance Type:                  HC1                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept     28.7588      2.324     12.376      0.0

In [762]:
m2 = ols('educ ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table(var1, 'educ', 'cov_med', 'cov_high')).fit(cov_type='HC1')
print(m2.summary())

                            OLS Regression Results                            
Dep. Variable:                   educ   R-squared:                       0.166
Model:                            OLS   Adj. R-squared:                  0.095
Method:                 Least Squares   F-statistic:                     3.801
Date:                Thu, 25 Apr 2024   Prob (F-statistic):            0.00930
Time:                        22:10:15   Log-Likelihood:                -195.99
No. Observations:                  52   AIC:                             402.0
Df Residuals:                      47   BIC:                             411.7
Df Model:                           4                                         
Covariance Type:                  HC1                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept     28.3333      2.214     12.796      0.0

In [763]:
# Define function for creating the regression table
def create_reg_table(var, new_var, x1, x2=None):
    # Pre-treatment data
    if (x2 != None):
        cols = [var + '_x', x1, x2]
    else:
        cols = [var + '_x', x1]
    df_before = a_gr_outcome[cols]
    df_before['t'] = 0
    df_before.rename({var + '_x': new_var}, axis=1, inplace=True)

    # Post-treatment data
    if (x2 != None):
        cols = [var + '_y', x1, x2]
    else:
        cols = [var + '_y', x1]
    df_after = a_gr_outcome[cols]
    df_after['t'] = 1
    df_after.rename({var + '_y': new_var}, axis=1, inplace=True)

    # Merged data
    df_reg = pd.concat([df_before, df_after])
    df_reg.dropna(inplace=True)
    
    return df_reg

In [764]:
var1 = 'EDEDUCMNED'
a = create_reg_table(var1, 'educ', 'treated')
print(ols('educ ~ treated + t + treated*t', data=a).fit(cov_type='HC1').summary())

                            OLS Regression Results                            
Dep. Variable:                   educ   R-squared:                       0.047
Model:                            OLS   Adj. R-squared:                 -0.096
Method:                 Least Squares   F-statistic:                    0.3038
Date:                Thu, 25 Apr 2024   Prob (F-statistic):              0.822
Time:                        22:10:15   Log-Likelihood:                -88.742
No. Observations:                  24   AIC:                             185.5
Df Residuals:                      20   BIC:                             190.2
Df Model:                           3                                         
Covariance Type:                  HC1                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept      8.8667      4.255      2.084      0.0

---

# Extra: Province-Level Analysis

In [765]:
# Create dataframe of dummy variables per project
prov = counties['Province'].value_counts().index
df_by_project = pd.DataFrame(columns=prov)
for i in range(len(kenya_trials_final['Province'])):
    temp_list = []
    for j in prov:
        if (j in kenya_trials_final['Province'].iloc[i]):
            temp_list.append(1)
        else:
            temp_list.append(0)
    df_by_project.loc[kenya_trials_final['RCT_ID'].iloc[i]] = temp_list

In [766]:
df_by_project = df_by_project.rename_axis(None, axis=1)
df_by_project.head()

Rift Valley  Eastern  Coast  Nyanza  Central  Western  \
AEARCTR-0000016            0        0      0       0        0        0   
AEARCTR-0000017            0        0      0       1        0        0   
AEARCTR-0000019            0        0      0       1        0        0   
AEARCTR-0000067            0        0      0       0        0        1   
AEARCTR-0000105            0        1      0       0        0        0   

                 Northern  Nairobi  
AEARCTR-0000016         0        1  
AEARCTR-0000017         0        0  
AEARCTR-0000019         0        0  
AEARCTR-0000067         0        0  
AEARCTR-0000105         0        0

In [767]:
# Transpose project-level dataframe to get county-level dataframe
df_by_prov = df_by_project.T
df_by_prov.head()

AEARCTR-0000016  AEARCTR-0000017  AEARCTR-0000019  \
Rift Valley                0                0                0   
Eastern                    0                0                0   
Coast                      0                0                0   
Nyanza                     0                1                1   
Central                    0                0                0   

             AEARCTR-0000067  AEARCTR-0000105  AEARCTR-0000218  \
Rift Valley                0                0                0   
Eastern                    0                1                0   
Coast                      0                0                0   
Nyanza                     0                0                0   
Central                    0                0                0   

             AEARCTR-0000287  AEARCTR-0000323  AEARCTR-0000350  \
Rift Valley                0                0                0   
Eastern                    1                0                0   
Coast                      0                0                0   
Nyanza                     1                1                1   
Central                    0                0                0   

             AEARCTR-0000443  AEARCTR-0000459  AEARCTR-0000486  \
Rift Valley                0                0                0   
Eastern                    0                0                0   
Coast                      0                0                0   
Nyanza                     1                0                0   
Central                    1                0                0   

             AEARCTR-0000541  AEARCTR-0000605  AEARCTR-0000627  \
Rift Valley                0                0                0   
Eastern                    0                0                0   
Coast                      0                0                0   
Nyanza                     1                0                0   
Central                    0                0                0   

             AEARCTR-0000647  AEARCTR-0000662  AEARCTR-0000669  \
Rift Valley                0                0                0   
Eastern                    0                0                0   
Coast                      0                0                0   
Nyanza                     0                1                1   
Central                    0                0                0   

             AEARCTR-0000676  AEARCTR-0000705  AEARCTR-0000740  \
Rift Valley                0                0                0   
Eastern                    0                0                0   
Coast                      0                0                0   
Nyanza                     0                0                0   
Central                    0                1                0   

             AEARCTR-0000766  AEARCTR-0000788  AEARCTR-0000790  \
Rift Valley                0                0                0   
Eastern                    0                0                0   
Coast                      0                0                0   
Nyanza                     0                0                0   
Central                    0                0                0   

             AEARCTR-0000791  AEARCTR-0000843  AEARCTR-0000844  \
Rift Valley                0                0                0   
Eastern                    0                0                0   
Coast                      0                0                0   
Nyanza                     0                0                0   
Central                    0                0                0   

             AEARCTR-0000893  AEARCTR-0000907  AEARCTR-0000912  \
Rift Valley                0                0                0   
Eastern                    0                0                0   
Coast                      0                0                0   
Nyanza                     0                0                0   
Central                    0                0                0   

             AEARCTR-0000934  AEARCTR-00009

In [768]:
# Reset index and rename column for both dataframes
df_by_project = df_by_project.reset_index().rename({'index': 'RCT_ID'}, axis=1)
df_by_prov = df_by_prov.reset_index().rename({'index': 'Province'}, axis=1)

In [769]:
# Convert dates to Pandas datetime format
kenya_trials_final[['Start date', 'End date']] = kenya_trials[['Start date', 'End date']].apply(pd.to_datetime)
df_by_project = df_by_project.merge(kenya_trials_final[['RCT_ID', 'Start date', 'End date']], how='left', on='RCT_ID')
df_by_project.head()

RCT_ID  Rift Valley  Eastern  Coast  Nyanza  Central  Western  \
0  AEARCTR-0000016            0        0      0       0        0        0   
1  AEARCTR-0000017            0        0      0       1        0        0   
2  AEARCTR-0000019            0        0      0       1        0        0   
3  AEARCTR-0000067            0        0      0       0        0        1   
4  AEARCTR-0000105            0        1      0       0        0        0   

   Northern  Nairobi Start date   End date  
0         0        1 2012-07-16 2013-02-14  
1         0        0 2011-05-01 2013-02-28  
2         0        0 2011-05-01 2013-02-28  
3         0        0 2012-08-01 2014-08-15  
4         0        0 2013-02-01 2017-03-31

In [770]:
df_by_project.shape

# 154 total projects after all the data cleaning (projects removed mainly because of lack of location information)

(154, 11)

In [771]:
min(df_by_project['Start date'])

Timestamp('2000-06-01 00:00:00')

In [772]:
max(df_by_project['End date'])

Timestamp('2027-12-31 00:00:00')

- Earliest start date is in 2000 and latest end date is in 2027
- Don't have to restrict time period as we have all the required data at the province-level
- The treatment group should consist of provinces that only started after 2000 (i.e. all projects) and the control group should consist of provinces where no projects were implemented
- Latest end date should be 2022 to measure treatment effect
- Define coverage variable: for what portion of the 8-year period did the project run?
- <font color='green'> Would it make more sense to restrict to projects that ended by 2022? Completion of projects affects treatment effect? (reasonable) </font>

In [773]:
# Restrict start date to before 2023
restricted_project = df_by_project[(df_by_project['Start date'].dt.year > 2003) & (df_by_project['Start date'].dt.year < 2023)]
restricted_project.head()

RCT_ID  Rift Valley  Eastern  Coast  Nyanza  Central  Western  \
0  AEARCTR-0000016            0        0      0       0        0        0   
1  AEARCTR-0000017            0        0      0       1        0        0   
2  AEARCTR-0000019            0        0      0       1        0        0   
3  AEARCTR-0000067            0        0      0       0        0        1   
4  AEARCTR-0000105            0        1      0       0        0        0   

   Northern  Nairobi Start date   End date  
0         0        1 2012-07-16 2013-02-14  
1         0        0 2011-05-01 2013-02-28  
2         0        0 2011-05-01 2013-02-28  
3         0        0 2012-08-01 2014-08-15  
4         0        0 2013-02-01 2017-03-31

In [774]:
restricted_project.shape

# Removed 14 projects

(136, 11)

In [775]:
# Define coverage variable: for what portion of the years did the study run?
cov = []

for i in range(len(restricted_project)):
    row = restricted_project.iloc[i]
    if row['End date'].year < 2023:
        val = (row['End date'].year - row['Start date'].year)/20
    else:
        val = (2023 - row['Start date'].year)/23 # as we are only considering coverage during our time period of interest: 2000 to 2022
    cov.append(val)

restricted_project['Coverage'] = cov
min(restricted_project['Coverage']), max(restricted_project['Coverage'])

(0.0, 0.65)

In [836]:
restricted_project[restricted_project['Coverage'] == 0.65]

RCT_ID  Rift Valley  Eastern  Coast  Nyanza  Central  Western  \
142  AEARCTR-0011184            0        0      0       0        0        0   

     Northern  Nairobi Start date   End date  Coverage  
142         1        0 2009-10-01 2022-02-28      0.65

- Longest project: https://www.socialscienceregistry.org/trials/11184

In [777]:
# Create dataset at the project-county level
df_prov_project = pd.melt(restricted_project, id_vars=['RCT_ID', 'Start date', 'End date', 'Coverage'], var_name='Province', value_name='Number Projects')
df_prov_project

RCT_ID Start date   End date  Coverage     Province  \
0     AEARCTR-0000016 2012-07-16 2013-02-14  0.050000  Rift Valley   
1     AEARCTR-0000017 2011-05-01 2013-02-28  0.100000  Rift Valley   
2     AEARCTR-0000019 2011-05-01 2013-02-28  0.100000  Rift Valley   
3     AEARCTR-0000067 2012-08-01 2014-08-15  0.100000  Rift Valley   
4     AEARCTR-0000105 2013-02-01 2017-03-31  0.200000  Rift Valley   
5     AEARCTR-0000218 2013-05-28 2013-08-07  0.000000  Rift Valley   
6     AEARCTR-0000287 2013-06-01 2018-06-01  0.250000  Rift Valley   
7     AEARCTR-0000323 2014-01-27 2014-10-26  0.000000  Rift Valley   
8     AEARCTR-0000350 2014-02-07 2020-08-31  0.300000  Rift Valley   
9     AEARCTR-0000443 2013-12-10 2016-06-30  0.150000  Rift Valley   
10    AEARCTR-0000459 2013-05-31 2015-12-31  0.100000  Rift Valley   
11    AEARCTR-0000486 2014-08-25 2015-08-25  0.050000  Rift Valley   
12    AEARCTR-0000541 2014-11-10 2016-04-30  0.100000  Rift Valley   
13    AEARCTR-0000605 2015-01-28 2015-08-15  0.000000  Rift Valley   
14    AEARCTR-0000627 2014-11-01 2014-12-31  0.000000  Rift Valley   
15    AEARCTR-0000647 2011-03-01 2013-04-30  0.100000  Rift Valley   
16    AEARCTR-0000662 2015-05-04 2016-09-15  0.050000  Rift Valley   
17    AEARCTR-0000669 2015-04-14 2016-09-15  0.050000  Rift Valley   
18    AEARCTR-0000676 2015-04-08 2016-12-31  0.050000  Rift Valley   
19    AEARCTR-0000705 2010-10-01 2014-06-01  0.200000  Rift Valley   
20    AEARCTR-0000740 2009-08-01 2015-06-18  0.300000  Rift Valley   
21    AEARCTR-0000766 2015-04-25 2015-06-15  0.000000  Rift Valley   
22    AEARCTR-0000788 2014-09-15 2016-01-01  0.100000  Rift Valley   
23    AEARCTR-0000790 2015-06-29 2015-09-01  0.000000  Rift Valley   
24    AEARCTR-0000791 2015-02-01 2015-07-01  0.000000  Rift Valley   
25    AEARCTR-0000843 2015-09-15 2018-08-31  0.150000  Rift Valley   
26    AEARCTR-0000844 2015-09-15 2017-03-22  0.100000  Rift Valley   
27    AEARCTR-0000893 2014-05-01 2014-08-01  0.000000  Rift Valley   
28    AEARCTR-0000907 2015-10-08 2015-11-30  0.000000  Rift Valley   
29    AEARCTR-0000912 2015-06-11 2016-04-01  0.050000  Rift Valley   
30    AEARCTR-0000934 2013-02-01 2015-12-31  0.100000  Rift Valley   
31    AEARCTR-0000946 2011-03-01 2013-01-31  0.100000  Rift Valley   
32    AEARCTR-0000962 2015-01-13 2019-12-31  0.200000  Rift Valley   
33    AEARCTR-0000991 2015-07-01 2016-06-01  0.050000  Rift Valley   
34    AEARCTR-0000996 2016-01-11 2024-12-31  0.304348  Rift Valley   
35    AEARCTR-0001002 2010-01-01 2016-03-01  0.300000  Rift Valley   
36    AEARCTR-0001008 2015-10-01 2016-01-01  0.050000  Rift Valley   
37    AEARCTR-0001076 2007-11-12 2010-08-31  0.150000  Rift Valley   
38    AEARCTR-0001167 2007-02-01 2007-08-31  0.000000  Rift Valley   
39    AEARCTR-0001183 2005-10-01 2007-02-28  0.100000  Rift Valley   
40    AEARCTR-0001187 2016-06-01 2018-04-01  0.100000  Rift Valley   
41    AEARCTR-0001197 2010-01-01 2010-05-31  0.000000  Rift Valley   
42    AEARCTR-0001293 2014-06-01 2018-01-01  0.200000  Rift Valley   
43    AEARCTR-0001304 2005-03-01 2007-11-30  0.100000  Rift Valley   
44    AEARCTR-0001358 2009-05-01 2012-12-31  0.150000  Rift Valley   
45    AEARCTR-0001373 2017-04-03 2018-07-31  0.050000  Rift Valley   
46    AEARCTR-0001457 2015-06-01 2015-11-28  0.000000  Rift Valley   
47    AEARCTR-0001482 2016-01-01 2017-08-01  0.050000  Rift Valley   
48    AEARCTR-0001484 2016-07-04 2020-12-31  0.200000  Rift Valley   
49    AEARCTR-0001500 2016-09-19 2017-12-31  0.050000  Rift Valley   
50    AEARCTR-0001515 2015-01-01 2016-07-01  0.050000  Rift Valley   
51    AEARCTR-0001574 2016-09-14 2016-09-26  0.000000  Rift Valley   
52    AEARCTR-0001592 2006-02-01 2013-01-01  0.350000  Rift Valley   
53    AEARCTR-0001643 2016-09-05 2017-12-31  0.050000  Rift Valley   
54    AEARCTR-0001706 2009-10-01 2014-01-15  0.250000  Rift Valley   
55    AEARCTR-0001824 2009-07-01 2013-08-31  0.200000  Rift Valley   
56    AEARCTR-0001848 201

In [778]:
df_prov_project.shape #140 * 8 --> makes sense

(1088, 6)

In [779]:
# Find total number of projects for each county
grouped_data = df_prov_project.groupby('Province').agg({'Number Projects': sum})
grouped_data

Number Projects
Province                    
Central                   10
Coast                      2
Eastern                   14
Nairobi                   52
Northern                   5
Nyanza                    21
Rift Valley                4
Western                   44

In [780]:
# Compute coverage by province
province_cov = []
for prov in grouped_data.reset_index()['Province']:
    subset = df_prov_project[df_prov_project['Province'] == prov]
    if sum(subset['Number Projects']) == 0:
        province_cov.append(0)
    else:
        cov = np.mean(subset[subset['Number Projects'] > 0]['Coverage'])
        province_cov.append(cov)

In [781]:
# Transpose project-level dataframe to get county-level dataframe
restricted_prov = restricted_project.iloc[:, :9].set_index('RCT_ID').T.reset_index().rename_axis(None, axis=1).rename({'index': 'Province'}, axis=1)
restricted_prov.sort_values(by='Province', inplace=True)
restricted_prov['Coverage'] = province_cov
restricted_prov

Province  AEARCTR-0000016  AEARCTR-0000017  AEARCTR-0000019  \
4      Central                0                0                0   
2        Coast                0                0                0   
1      Eastern                0                0                0   
7      Nairobi                1                0                0   
6     Northern                0                0                0   
3       Nyanza                0                1                1   
0  Rift Valley                0                0                0   
5      Western                0                0                0   

   AEARCTR-0000067  AEARCTR-0000105  AEARCTR-0000218  AEARCTR-0000287  \
4                0                0                0                0   
2                0                0                0                0   
1                0                1                0                1   
7                0                0                1                0   
6                0                0                0                0   
3                0                0                0                1   
0                0                0                0                0   
5                1                0                0                1   

   AEARCTR-0000323  AEARCTR-0000350  AEARCTR-0000443  AEARCTR-0000459  \
4                0                0                1                0   
2                0                0                0                0   
1                0                0                0                0   
7                0                0                0                1   
6                0                0                0                0   
3                1                1                1                0   
0                0                0                0                0   
5                0                1                1                0   

   AEARCTR-0000486  AEARCTR-0000541  AEARCTR-0000605  AEARCTR-0000627  \
4                0                0                0                0   
2                0                0                0                0   
1                0                0                0                0   
7                0                0                1                1   
6                0                0                0                0   
3                0                1                0                0   
0                0                0                0                0   
5                1                0                0                0   

   AEARCTR-0000647  AEARCTR-0000662  AEARCTR-0000669  AEARCTR-0000676  \
4                0                0                0                0   
2                0                0                0                0   
1                0                0                0                0   
7                1                0                0                1   
6                0                0                0                0   
3                0                1                1                0   
0                0                0                0                0   
5                0                0                0                0   

   AEARCTR-0000705  AEARCTR-0000740  AEARCTR-0000766  AEARCTR-0000788  \
4                1                0                0                0   
2                0                0                0                0   
1                0                0                0                0   
7                0                0                1                1   
6                0                0                0                0   
3                0                0                0                0   
0                0                0                0                0   
5                0                1                0                0   

   AEARCTR-0000790  AEARCTR-0000791  AEARCTR-0000843  AEARCTR-0000844  \
4                0   

In [782]:
restricted_prov.shape

(8, 138)

In [783]:
# Merge with county-level data
restricted_prov = restricted_prov.merge(grouped_data.reset_index(), on='Province', how='left')
restricted_prov

Province  AEARCTR-0000016  AEARCTR-0000017  AEARCTR-0000019  \
0      Central                0                0                0   
1        Coast                0                0                0   
2      Eastern                0                0                0   
3      Nairobi                1                0                0   
4     Northern                0                0                0   
5       Nyanza                0                1                1   
6  Rift Valley                0                0                0   
7      Western                0                0                0   

   AEARCTR-0000067  AEARCTR-0000105  AEARCTR-0000218  AEARCTR-0000287  \
0                0                0                0                0   
1                0                0                0                0   
2                0                1                0                1   
3                0                0                1                0   
4                0                0                0                0   
5                0                0                0                1   
6                0                0                0                0   
7                1                0                0                1   

   AEARCTR-0000323  AEARCTR-0000350  AEARCTR-0000443  AEARCTR-0000459  \
0                0                0                1                0   
1                0                0                0                0   
2                0                0                0                0   
3                0                0                0                1   
4                0                0                0                0   
5                1                1                1                0   
6                0                0                0                0   
7                0                1                1                0   

   AEARCTR-0000486  AEARCTR-0000541  AEARCTR-0000605  AEARCTR-0000627  \
0                0                0                0                0   
1                0                0                0                0   
2                0                0                0                0   
3                0                0                1                1   
4                0                0                0                0   
5                0                1                0                0   
6                0                0                0                0   
7                1                0                0                0   

   AEARCTR-0000647  AEARCTR-0000662  AEARCTR-0000669  AEARCTR-0000676  \
0                0                0                0                0   
1                0                0                0                0   
2                0                0                0                0   
3                1                0                0                1   
4                0                0                0                0   
5                0                1                1                0   
6                0                0                0                0   
7                0                0                0                0   

   AEARCTR-0000705  AEARCTR-0000740  AEARCTR-0000766  AEARCTR-0000788  \
0                1                0                0                0   
1                0                0                0                0   
2                0                0                0                0   
3                0                0                1                1   
4                0                0                0                0   
5                0                0                0                0   
6                0                0                0                0   
7                0                1                0                0   

   AEARCTR-0000790  AEARCTR-0000791  AEARCTR-0000843  AEARCTR-0000844  \
0                0   

## Data on Outcome Variables

- Spatial data from DHS in 1998 and 2022

In [784]:
# Variables for regression

# Education
var1e = 'EDEDUCMCPR' # percentage of men with completed primary education *
var2e = 'EDEDUCMCSC' # percentage of men with completed secondary education *
var3e = 'EDEDUCMSPR' # percentage of men with some primary education
var4e = 'EDEDUCMSSC' # percentage of men with some secondary education
var5e = 'EDEDUCWCPR' # percentage of women with completed primary education *
var6e = 'EDEDUCWCSC' # percentage of women with completed secondary education *
var7e = 'EDEDUCWSPR' # percentage of women with some primary education
var8e = 'EDEDUCWSSC' # percentage of women with some secondary education

#Health
var1h = 'CHVACCCBAS' # percentage of children (12-23 months) who received all 8 basic vaccinations *
var2h = 'CMECMRCCMR' # child mortality rate *
var3h = 'CMECMRCIMR' # infant mortality rate
var4h = 'CMECMRCNNR' # neonatal mortality rate
var5h = 'CMECMRCPNR' # postneonatal mortality rate
var6h = 'CMECMRCU5M' # under-5 mortality rate
var7h = 'CNNUTSCHA2' # children stunted *
var8h = 'CNNUTSCWA2' # children underweight *
var9h = 'CNNUTSCWH2' # children wasted

In [785]:
# Define function for reading Shapefiles
def read_shapefile(sf_shape):
    """
    Read a shapefile into a Pandas dataframe with a 'coords' 
    column holding the geometry information. This uses the pyshp
    package
    """

    fields = [x[0] for x in sf_shape.fields][1:]
    records = [y[:] for y in sf_shape.records()]
    #records = sf_shape.records()
    shps = [s.points for s in sf_shape.shapes()]
    df = pd.DataFrame(columns=fields, data=records)
    df = df.assign(coords=shps)
    return df

In [786]:
# Read 1998 educ data
sh_educ_1998 = shapefile.Reader('sdr_subnational_data_dhs_1998.shp')
df_educ_1998 = read_shapefile(sh_educ_1998).rename({'DHSREGEN': 'Province', 
                                         var1e: var1e+'_1998',
                                         var2e: var2e+'_1998',
                                         var3e: var3e+'_1998',
                                         var4e: var4e+'_1998',
                                         var5e: var5e+'_1998',
                                         var6e: var6e+'_1998',
                                         var7e: var7e+'_1998',
                                         var8e: var8e+'_1998'}, axis=1)
df_educ_1998

ISO FIPS DHSCC SVYTYPE  SVYYEAR CNTRYNAMEE CNTRYNAMEF CNTRYNAMES  \
0  KE   KE    KE     DHS   1998.0      Kenya                         
1  KE   KE    KE     DHS   1998.0      Kenya                         
2  KE   KE    KE     DHS   1998.0      Kenya                         
3  KE   KE    KE     DHS   1998.0      Kenya                         
4  KE   KE    KE     DHS   1998.0      Kenya                         
5  KE   KE    KE     DHS   1998.0      Kenya                         
6  KE   KE    KE     DHS   1998.0      Kenya                         

       Province DHSREGFR DHSREGSP  SVYID           REG_ID Svy_Map MULTLEVEL  \
0  Nairobi Area                    115.0  KEDHS1998416001     yes        no   
1       Central                    115.0  KEDHS1998416002     yes        no   
2         Coast                    115.0  KEDHS1998416003     yes        no   
3       Eastern                    115.0  KEDHS1998416004     yes        no   
4        Nyanza                    115.0  KEDHS1998416005     yes        no   
5   Rift Valley                    115.0  KEDHS1998416006     yes        no   
6       Western                    115.0  KEDHS1998416007     yes        no   

   LEVELRNK REGVAR  REGCODE      REGNAME OTHREGVAR  OTHREGCO OTHREGNA LEVELCO  \
0       1.0  hv024      1.0      nairobi      NULL    9999.0     NULL  Admin1   
1       1.0  hv024      2.0      central      NULL    9999.0     NULL  Admin1   
2       1.0  hv024      3.0        coast      NULL    9999.0     NULL  Admin1   
3       1.0  hv024      4.0      eastern      NULL    9999.0     NULL  Admin1   
4       1.0  hv024      5.0       nyanza      NULL    9999.0     NULL  Admin1   
5       1.0  hv024      6.0  rift valley      NULL    9999.0     NULL  Admin1   
6       1.0  hv024      7.0      western      NULL    9999.0     NULL  Admin1   

     LEVELNA REPALLIND REGNOTES  \
0  Provinces        no            
1  Provinces        no            
2  Provinces        no            
3  Provinces        no            
4  Provinces        no            
5  Provinces        no            
6  Provinces        no            

                                            SVYNOTES  EDGARPWFEM  EDGARPMMAL  \
0  7 regions as 8 admin1 areas, minus the North E...      9999.0      9999.0   
1  7 regions as 8 admin1 areas, minus the North E...      9999.0      9999.0   
2  7 regions as 8 admin1 areas, minus the North E...      9999.0      9999.0   
3  7 regions as 8 admin1 areas, minus the North E...      9999.0      9999.0   
4  7 regions as 8 admin1 areas, minus the North E...      9999.0      9999.0   
5  7 regions as 8 admin1 areas, minus the North E...      9999.0      9999.0   
6  7 regions as 8 admin1 areas, minus the North E...      9999.0      9999.0   

   EDGARPBBTH  EDGARSWFEM  EDGARSMMAL  EDGARSBBTH  EDGARSBGPI  EDEDUCWNED  \
0      9999.0      9999.0      9999.0      9999.0      9999.0         1.2   
1      9999.0      9999.0      9999.0      9999.0      9999.0         4.7   
2      9999.0      9999.0      9999.0      9999.0      9999.0        30.6   
3      9999.0      9999.0      9999.0      9999.0      9999.0        10.0   
4      9999.0      9999.0      9999.0      9999.0      9999.0        10.7   
5      9999.0      9999.0      9999.0      9999.0      9999.0        14.5   
6      9999.0      9999.0      9999.0      9999.0      9999.0        12.2   

   EDEDUCWSPR_1998  EDEDUCWCPR_1998  EDEDUCWSSC_1998  EDEDUCWCSC_1998  \
0             21.0             23.4             10.7             34.1   
1             29.1             32.0             12.6             20.5   
2             26.5             21.8              7.8             12.2   
3             39.3             25.7              9.9             13.8   
4             47.2             16.6             13.2             11.4   
5             39.2             21.7              9.3             13.4   
6             35.7             21.6             15.3             12.2   

   EDEDUCWHGH  EDEDUCWDKM  EDEDUCWT

In [787]:
# Read 1998 health data
sh_health_1998 = shapefile.Reader('sdr_subnational_data_dhs_1998 1.shp')
df_health_1998 = read_shapefile(sh_health_1998).rename({'DHSREGEN': 'Province',
                                                             var1h: var1h+'_1998',
                                                             var2h: var2h+'_1998',
                                                             var3h: var3h+'_1998',
                                                             var4h: var4h+'_1998',
                                                             var5h: var5h+'_1998',
                                                             var6h: var6h+'_1998',
                                                             var7h: var7h+'_1998',
                                                             var8h: var8h+'_1998',
                                                             var9h: var9h+'_1998'}, axis=1)
df_health_1998

ISO FIPS DHSCC SVYTYPE  SVYYEAR CNTRYNAMEE CNTRYNAMEF CNTRYNAMES  \
0  KE   KE    KE     DHS   1998.0      Kenya                         
1  KE   KE    KE     DHS   1998.0      Kenya                         
2  KE   KE    KE     DHS   1998.0      Kenya                         
3  KE   KE    KE     DHS   1998.0      Kenya                         
4  KE   KE    KE     DHS   1998.0      Kenya                         
5  KE   KE    KE     DHS   1998.0      Kenya                         
6  KE   KE    KE     DHS   1998.0      Kenya                         

       Province DHSREGFR DHSREGSP  SVYID           REG_ID Svy_Map MULTLEVEL  \
0  Nairobi Area                    115.0  KEDHS1998416001     yes        no   
1       Central                    115.0  KEDHS1998416002     yes        no   
2         Coast                    115.0  KEDHS1998416003     yes        no   
3       Eastern                    115.0  KEDHS1998416004     yes        no   
4        Nyanza                    115.0  KEDHS1998416005     yes        no   
5   Rift Valley                    115.0  KEDHS1998416006     yes        no   
6       Western                    115.0  KEDHS1998416007     yes        no   

   LEVELRNK REGVAR  REGCODE      REGNAME OTHREGVAR  OTHREGCO OTHREGNA LEVELCO  \
0       1.0  hv024      1.0      nairobi      NULL    9999.0     NULL  Admin1   
1       1.0  hv024      2.0      central      NULL    9999.0     NULL  Admin1   
2       1.0  hv024      3.0        coast      NULL    9999.0     NULL  Admin1   
3       1.0  hv024      4.0      eastern      NULL    9999.0     NULL  Admin1   
4       1.0  hv024      5.0       nyanza      NULL    9999.0     NULL  Admin1   
5       1.0  hv024      6.0  rift valley      NULL    9999.0     NULL  Admin1   
6       1.0  hv024      7.0      western      NULL    9999.0     NULL  Admin1   

     LEVELNA REPALLIND REGNOTES  \
0  Provinces        no            
1  Provinces        no            
2  Provinces        no            
3  Provinces        no            
4  Provinces        no            
5  Provinces        no            
6  Provinces        no            

                                            SVYNOTES  CMECMRCNNR_1998  \
0  7 regions as 8 admin1 areas, minus the North E...             19.0   
1  7 regions as 8 admin1 areas, minus the North E...             18.0   
2  7 regions as 8 admin1 areas, minus the North E...             28.0   
3  7 regions as 8 admin1 areas, minus the North E...             23.0   
4  7 regions as 8 admin1 areas, minus the North E...             38.0   
5  7 regions as 8 admin1 areas, minus the North E...             28.0   
6  7 regions as 8 admin1 areas, minus the North E...             20.0   

   CMECMRCPNR_1998  CMECMRCIMR_1998  CMECMRCCMR_1998  CMECMRCU5M_1998  \
0             22.0             41.0             26.0             66.0   
1             10.0             27.0              6.0             33.0   
2             42.0             70.0             28.0             96.0   
3             31.0             53.0             26.0             78.0   
4             97.0            135.0             73.0            199.0   
5             22.0             50.0             18.0             68.0   
6             44.0             64.0             63.0            122.0   

   CHVACCCBAS_1998  CNNUTSCHA2_1998  CNNUTSCWH2_1998  CNNUTSCWA2_1998  \
0             50.0             28.7              8.4              7.7   
1             70.8             33.4              6.1             11.6   
2             67.7             42.9              5.5             21.9   
3             68.6             43.3              5.3             22.7   
4             44.4             35.8              8.4             18.7   
5             66.9             36.6              8.1             19.3   
6             51.2             40.0              4.8             15.5   

   MLNETCCITN  HACPHTWT1R  HACPHTMT1R  HAHIVPWHIV  HAHIVPMHIV  \
0      9999.0      9999.0      9999.0      9999.0      999

In [788]:
# Read 2003 data
sh_2003 = shapefile.Reader('sdr_subnational_data_dhs_2003.shp')
df_2003 = read_shapefile(sh_2003).rename({'DHSREGEN': 'Province', 
                                             var1e: var1e+'_2003',
                                             var2e: var2e+'_2003',
                                             var3e: var3e+'_2003',
                                             var4e: var4e+'_2003',
                                             var5e: var5e+'_2003',
                                             var6e: var6e+'_2003',
                                             var7e: var7e+'_2003',
                                             var8e: var8e+'_2003',
                                             var1h: var1h+'_2003',
                                             var2h: var2h+'_2003',
                                             var3h: var3h+'_2003',
                                             var4h: var4h+'_2003',
                                             var5h: var5h+'_2003',
                                             var6h: var6h+'_2003',
                                             var7h: var7h+'_2003',
                                             var8h: var8h+'_2003',
                                             var9h: var9h+'_2003'}, axis=1)
df_2003

ISO FIPS DHSCC SVYTYPE  SVYYEAR CNTRYNAMEE CNTRYNAMEF CNTRYNAMES  \
0  KE   KE    KE     DHS   2003.0      Kenya                         
1  KE   KE    KE     DHS   2003.0      Kenya                         
2  KE   KE    KE     DHS   2003.0      Kenya                         
3  KE   KE    KE     DHS   2003.0      Kenya                         
4  KE   KE    KE     DHS   2003.0      Kenya                         
5  KE   KE    KE     DHS   2003.0      Kenya                         
6  KE   KE    KE     DHS   2003.0      Kenya                         
7  KE   KE    KE     DHS   2003.0      Kenya                         

        Province DHSREGFR DHSREGSP  SVYID           REG_ID Svy_Map MULTLEVEL  \
0   Nairobi Area                    216.0  KEDHS2003416001     yes        no   
1        Central                    216.0  KEDHS2003416002     yes        no   
2          Coast                    216.0  KEDHS2003416003     yes        no   
3        Eastern                    216.0  KEDHS2003416004     yes        no   
4         Nyanza                    216.0  KEDHS2003416005     yes        no   
5    Rift Valley                    216.0  KEDHS2003416006     yes        no   
6        Western                    216.0  KEDHS2003416007     yes        no   
7  North-Eastern                    216.0  KEDHS2003416008     yes        no   

   LEVELRNK REGVAR  REGCODE        REGNAME OTHREGVAR  OTHREGCO OTHREGNA  \
0       1.0  hv024      1.0        nairobi      NULL    9999.0     NULL   
1       1.0  hv024      2.0        central      NULL    9999.0     NULL   
2       1.0  hv024      3.0          coast      NULL    9999.0     NULL   
3       1.0  hv024      4.0        eastern      NULL    9999.0     NULL   
4       1.0  hv024      5.0         nyanza      NULL    9999.0     NULL   
5       1.0  hv024      6.0    rift valley      NULL    9999.0     NULL   
6       1.0  hv024      7.0        western      NULL    9999.0     NULL   
7       1.0  hv024      8.0  north eastern      NULL    9999.0     NULL   

  LEVELCO    LEVELNA REPALLIND REGNOTES                         SVYNOTES  \
0  Admin1  Provinces        no           8 regions as the 8 admin1 areas   
1  Admin1  Provinces        no           8 regions as the 8 admin1 areas   
2  Admin1  Provinces        no           8 regions as the 8 admin1 areas   
3  Admin1  Provinces        no           8 regions as the 8 admin1 areas   
4  Admin1  Provinces        no           8 regions as the 8 admin1 areas   
5  Admin1  Provinces        no           8 regions as the 8 admin1 areas   
6  Admin1  Provinces        no           8 regions as the 8 admin1 areas   
7  Admin1  Provinces        no           8 regions as the 8 admin1 areas   

   CMECMRCNNR_2003  CMECMRCPNR_2003  CMECMRCIMR_2003  CMECMRCCMR_2003  \
0             32.0             35.0             67.0             30.0   
1             27.0             17.0             44.0             10.0   
2             45.0             33.0             78.0             41.0   
3             32.0             24.0             56.0             29.0   
4             27.0            106.0            133.0             84.0   
5             37.0             25.0             61.0             17.0   
6             25.0             54.0             80.0             70.0   
7             50.0             41.0             91.0             79.0   

   CMECMRCU5M_2003  CHVACCCBAS_2003  CNNUTSCHA2_2003  CNNUTSCWH2_2003  \
0             95.0             54.9             23.5              4.4   
1             54.0             70.8             31.1              4.5   
2            116.0             62.1             41.2              5.7   
3             84.0             59.3             39.2              4.7   
4            206.0             32.7             36.0              3.0   
5             77.0             51.5             37.0              7.8   
6            144.0             45.4             35.4              5.8   
7            163.0              7.5            

In [789]:
# Read 2022 educ data
sh_educ_2022 = shapefile.Reader('sdr_subnational_data_dhs_2022.shp')
df_educ_2022 = read_shapefile(sh_educ_2022).rename({'DHSREGEN': 'County'}, axis=1)

# Take average across counties to find province-level data for 2022
df_educ_2022 = df_educ_2022.merge(counties, on='County', how='left')
df_educ_2022_grp = df_educ_2022.groupby('Province')[[var1e, var2e, var3e, var4e, var5e, var6e, var7e, var8e]].agg(np.mean).reset_index().rename({'DHSREGEN': 'Province', 
                                                                                                                                                     var1e: var1e+'_2022',
                                                                                                                                                     var2e: var2e+'_2022',
                                                                                                                                                     var3e: var3e+'_2022',
                                                                                                                                                     var4e: var4e+'_2022',
                                                                                                                                                     var5e: var5e+'_2022',
                                                                                                                                                     var6e: var6e+'_2022',
                                                                                                                                                     var7e: var7e+'_2022',
                                                                                                                                                     var8e: var8e+'_2022'}, axis=1)
df_educ_2022_grp

Province  EDEDUCMCPR_2022  EDEDUCMCSC_2022  EDEDUCMSPR_2022  \
0      Central        20.540000        25.140000        14.080000   
1        Coast        22.560000        17.920000        25.060000   
2      Eastern        19.162500        17.675000        19.950000   
3      Nairobi        11.000000        30.900000         4.500000   
4     Northern         9.700000        16.400000        19.300000   
5       Nyanza        20.066667        18.166667        22.300000   
6  Rift Valley        15.171429        19.535714        19.421429   
7      Western        18.225000        14.850000        28.525000   

   EDEDUCMSSC_2022  EDEDUCWCPR_2022  EDEDUCWCSC_2022  EDEDUCWSPR_2022  \
0        20.620000        23.280000        24.940000        10.100000   
1        14.100000        20.400000        12.900000        26.720000   
2        21.837500        21.312500        16.175000        16.500000   
3        12.000000        14.700000        28.600000         6.600000   
4        17.700000         5.300000         7.566667        12.266667   
5        22.816667        23.333333        16.950000        22.300000   
6        19.971429        16.757143        17.514286        18.607143   
7        24.225000        19.950000        15.575000        25.350000   

   EDEDUCWSSC_2022  
0        20.720000  
1        12.260000  
2        19.150000  
3        13.800000  
4        10.333333  
5        25.566667  
6        17.378571  
7        25.350000

In [790]:
# Read 2022 health data
sh_health_2022 = shapefile.Reader('sdr_subnational_data_dhs_2022 1.shp')
df_health_2022 = read_shapefile(sh_health_2022).rename({'DHSREGEN': 'County'}, axis=1)

# Take average across counties to find province-level data for 2022
df_health_2022 = df_health_2022.merge(counties, on='County', how='left')
df_health_2022_grp = df_health_2022.groupby('Province')[[var1h, var2h, var3h, var4h, var5h, var6h, var7h, var8h, var9h]].agg(np.mean).reset_index().rename({'DHSREGEN': 'Province',
                                                                                                                                                                 var1h: var1h+'_2022',
                                                                                                                                                                 var2h: var2h+'_2022',
                                                                                                                                                                 var3h: var3h+'_2022',
                                                                                                                                                                 var4h: var4h+'_2022',
                                                                                                                                                                 var5h: var5h+'_2022',
                                                                                                                                                                 var6h: var6h+'_2022',
                                                                                                                                                                 var7h: var7h+'_2022',
                                                                                                                                                                 var8h: var8h+'_2022',
                                                                                                                                                                 var9h: var9h+'_2022'}, axis=1)
df_health_2022_grp

Province  CHVACCCBAS_2022  CMECMRCCMR_2022  CMECMRCIMR_2022  \
0      Central        88.700000         5.400000        43.400000   
1        Coast        79.920000         7.600000        35.800000   
2      Eastern        81.037500         6.125000        26.125000   
3      Nairobi        77.200000         4.000000        40.000000   
4     Northern        33.533333         6.333333        34.666667   
5       Nyanza        83.466667        15.500000        39.166667   
6  Rift Valley        76.142857         7.571429        33.071429   
7      Western        89.175000        17.750000        33.750000   

   CMECMRCNNR_2022  CMECMRCPNR_2022  CMECMRCU5M_2022  CNNUTSCHA2_2022  \
0        29.600000        13.600000        48.000000        13.380000   
1        24.800000        10.600000        43.000000        22.080000   
2        18.375000         7.500000        32.250000        19.962500   
3        20.000000        20.000000        44.000000        11.100000   
4        27.000000         7.666667        40.666667        13.966667   
5        27.000000        12.500000        54.000000        14.233333   
6        21.428571        11.642857        40.214286        20.678571   
7        19.750000        14.000000        51.000000        15.525000   

   CNNUTSCWA2_2022  CNNUTSCWH2_2022  
0         5.120000         2.340000  
1        14.460000         6.560000  
2        12.237500         6.800000  
3         5.300000         2.500000  
4        17.833333        18.466667  
5         5.466667         2.166667  
6        14.600000         7.121429  
7         7.875000         2.250000

In [791]:
# Read 2022 health data
sh_1993 = shapefile.Reader('sdr_subnational_data_dhs_1993.shp')
df_1993 = read_shapefile(sh_1993).rename({'DHSREGEN': 'Province'}, axis=1)
df_1993

ISO FIPS DHSCC SVYTYPE  SVYYEAR CNTRYNAMEE CNTRYNAMEF CNTRYNAMES  \
0  KE   KE    KE     DHS   1993.0      Kenya                         
1  KE   KE    KE     DHS   1993.0      Kenya                         
2  KE   KE    KE     DHS   1993.0      Kenya                         
3  KE   KE    KE     DHS   1993.0      Kenya                         
4  KE   KE    KE     DHS   1993.0      Kenya                         
5  KE   KE    KE     DHS   1993.0      Kenya                         
6  KE   KE    KE     DHS   1993.0      Kenya                         

       Province DHSREGFR DHSREGSP  SVYID           REG_ID Svy_Map MULTLEVEL  \
0  Nairobi Area                     56.0  KEDHS1993416001     yes        no   
1       Central                     56.0  KEDHS1993416002     yes        no   
2         Coast                     56.0  KEDHS1993416003     yes        no   
3       Eastern                     56.0  KEDHS1993416004     yes        no   
4        Nyanza                     56.0  KEDHS1993416005     yes        no   
5   Rift Valley                     56.0  KEDHS1993416006     yes        no   
6       Western                     56.0  KEDHS1993416007     yes        no   

   LEVELRNK REGVAR  REGCODE      REGNAME OTHREGVAR  OTHREGCO OTHREGNA LEVELCO  \
0       1.0  hv024      1.0      nairobi      NULL    9999.0     NULL  Admin1   
1       1.0  hv024      2.0      central      NULL    9999.0     NULL  Admin1   
2       1.0  hv024      3.0        coast      NULL    9999.0     NULL  Admin1   
3       1.0  hv024      4.0      eastern      NULL    9999.0     NULL  Admin1   
4       1.0  hv024      5.0       nyanza      NULL    9999.0     NULL  Admin1   
5       1.0  hv024      6.0  rift valley      NULL    9999.0     NULL  Admin1   
6       1.0  hv024      7.0      western      NULL    9999.0     NULL  Admin1   

     LEVELNA REPALLIND REGNOTES  \
0  Provinces       yes            
1  Provinces       yes            
2  Provinces       yes            
3  Provinces       yes            
4  Provinces       yes            
5  Provinces       yes            
6  Provinces       yes            

                                            SVYNOTES  CMECMTCNNR  CMECMTCPNR  \
0  7 regions as 8 admin1 areas, minus the North E...      9999.0      9999.0   
1  7 regions as 8 admin1 areas, minus the North E...      9999.0      9999.0   
2  7 regions as 8 admin1 areas, minus the North E...      9999.0      9999.0   
3  7 regions as 8 admin1 areas, minus the North E...      9999.0      9999.0   
4  7 regions as 8 admin1 areas, minus the North E...      9999.0      9999.0   
5  7 regions as 8 admin1 areas, minus the North E...      9999.0      9999.0   
6  7 regions as 8 admin1 areas, minus the North E...      9999.0      9999.0   

   CMECMTCIMR  CMECMTCCMR  CMECMTCU5M  CHVACCCBAS  CNNUTSCHA2  CNNUTSCWH2  \
0      9999.0      9999.0      9999.0        86.7        32.2         1.7   
1      9999.0      9999.0      9999.0        91.2        37.5         4.9   
2      9999.0      9999.0      9999.0        80.9        48.1        11.9   
3      9999.0      9999.0      9999.0        84.5        47.6         7.8   
4      9999.0      9999.0      9999.0        69.7        39.4         5.9   
5      9999.0      9999.0      9999.0        75.7        34.9         8.4   
6      9999.0      9999.0      9999.0        68.0        36.7         3.9   

   CNNUTSCWA2  EDEDATWSPR  EDEDATWCPR  EDEDATWSSC  EDEDATWCSC  EDEDATMSPR  \
0         8.5        22.1        24.1        35.0         2.2        23.4   
1        15.0        45.1        19.7        13.3         0.5        47.0   
2        29.7        34.1        13.6         8.6         0.2        40.6   
3        23.6        47.0        15.3         9.7         0.1        52.4   
4        17.3        49.2        13.0         7.9         0.4        52.2   
5        19.8        47.0        13.3         9.3         0.4        46.5   
6        12.6        47.7        14.5        11.9         0.4        48.5   

   

In [792]:
# Add column to indicate treatment status
restricted_prov['treated_num'] = [0 if restricted_prov['Number Projects'].iloc[i] == 0 else 1 for i in range(len(restricted_prov))]
restricted_prov['treated_cov'] = [0 if restricted_prov['Coverage'].iloc[i] == 0 else 1 for i in range(len(restricted_prov))]

In [793]:
# Discretize treatment variables

# Discretize number of projects into 3 categories: low, medium, high
num_low, num_med, num_high = [], [], []
for i in restricted_prov['Number Projects']:
    if i <= 5:
        num_low.append(1)
        num_med.append(0)
        num_high.append(0)
    elif (i > 5 and i < 20):
        num_low.append(0)
        num_med.append(1)
        num_high.append(0)
    elif (i >= 20):
        num_low.append(0)
        num_med.append(0)
        num_high.append(1)
        
restricted_prov['num_low'] = num_low
restricted_prov['num_med'] = num_med
restricted_prov['num_high'] = num_high

In [796]:
# Discretize treatment variables

# Discretize number of projects into 3 categories: low, medium, high
control, treat = [], []
for i in restricted_prov['Number Projects']:
    if i <= 5:
        control.append(1)
        treat.append(0)
    elif i > 5:
        control.append(0)
        treat.append(1)
        
restricted_prov['control'] = control
restricted_prov['treat'] = treat

In [797]:
# Discretize coverage into 3 categories: low, medium, high
cov_low, cov_med, cov_high = [], [], []
for i in restricted_prov['Coverage']:
    if i <= 0.05:
        cov_low.append(1)
        cov_med.append(0)
        cov_high.append(0)
    elif (i > 0.05 and i < 0.1):
        cov_low.append(0)
        cov_med.append(1)
        cov_high.append(0)
    else:
        cov_low.append(0)
        cov_med.append(0)
        cov_high.append(1)
        
restricted_prov['cov_low'] = cov_low
restricted_prov['cov_med'] = cov_med
restricted_prov['cov_high'] = cov_high

In [857]:
df_2003.sort_values(by='Province',inplace=True)
df_2003['Province'] = counties['Province'].value_counts().index.sort_values()

In [858]:
# Merge data on trials with data on outcome variables
restricted_prov_outcome = restricted_prov.merge(df_educ_1998, on='Province', how='left').merge(df_educ_2022_grp, on='Province', how='left').merge(df_health_1998, on='Province', how='left').merge(df_health_2022_grp, on='Province', how='left').merge(df_2003, on='Province', how='left')
restricted_prov_outcome

Province  AEARCTR-0000016  AEARCTR-0000017  AEARCTR-0000019  \
0      Central                0                0                0   
1        Coast                0                0                0   
2      Eastern                0                0                0   
3      Nairobi                1                0                0   
4     Northern                0                0                0   
5       Nyanza                0                1                1   
6  Rift Valley                0                0                0   
7      Western                0                0                0   

   AEARCTR-0000067  AEARCTR-0000105  AEARCTR-0000218  AEARCTR-0000287  \
0                0                0                0                0   
1                0                0                0                0   
2                0                1                0                1   
3                0                0                1                0   
4                0                0                0                0   
5                0                0                0                1   
6                0                0                0                0   
7                1                0                0                1   

   AEARCTR-0000323  AEARCTR-0000350  AEARCTR-0000443  AEARCTR-0000459  \
0                0                0                1                0   
1                0                0                0                0   
2                0                0                0                0   
3                0                0                0                1   
4                0                0                0                0   
5                1                1                1                0   
6                0                0                0                0   
7                0                1                1                0   

   AEARCTR-0000486  AEARCTR-0000541  AEARCTR-0000605  AEARCTR-0000627  \
0                0                0                0                0   
1                0                0                0                0   
2                0                0                0                0   
3                0                0                1                1   
4                0                0                0                0   
5                0                1                0                0   
6                0                0                0                0   
7                1                0                0                0   

   AEARCTR-0000647  AEARCTR-0000662  AEARCTR-0000669  AEARCTR-0000676  \
0                0                0                0                0   
1                0                0                0                0   
2                0                0                0                0   
3                1                0                0                1   
4                0                0                0                0   
5                0                1                1                0   
6                0                0                0                0   
7                0                0                0                0   

   AEARCTR-0000705  AEARCTR-0000740  AEARCTR-0000766  AEARCTR-0000788  \
0                1                0                0                0   
1                0                0                0                0   
2                0                0                0                0   
3                0                0                1                1   
4                0                0                0                0   
5                0                0                0                0   
6                0                0                0                0   
7                0                1                0                0   

   AEARCTR-0000790  AEARCTR-0000791  AEARCTR-0000843  AEARCTR-0000844  \
0                0   

# Descriptive Analysis

## Summary Statistics

### Treatment Variables

In [822]:
restricted_prov[['Province', 'Number Projects', 'Coverage']]

Province  Number Projects  Coverage
0      Central               10  0.144348
1        Coast                2  0.000000
2      Eastern               14  0.076242
3      Nairobi               52  0.058236
4     Northern                5  0.250000
5       Nyanza               21  0.097516
6  Rift Valley                4  0.087500
7      Western               44  0.121937

### Outcome Variables

#### 1. Education

In [865]:
# 1998 data
df_educ_1998[[var1e+'_1998', var2e+'_1998', var3e+'_1998', var4e+'_1998', var5e+'_1998', var6e+'_1998', var7e+'_1998', var8e+'_1998']].describe().T

count       mean       std   min    25%   50%    75%   max
EDEDUCMCPR_1998    7.0  24.728571  5.569475  18.7  20.20  25.7  26.90  34.5
EDEDUCMCSC_1998    7.0  25.185714  8.261644  19.2  20.15  22.5  25.70  42.9
EDEDUCMSPR_1998    7.0  29.185714  9.410885  13.0  24.75  30.6  35.20  40.8
EDEDUCMSSC_1998    7.0  13.142857  2.724492   9.9  10.85  13.0  15.55  16.3
EDEDUCWCPR_1998    7.0  23.257143  4.726471  16.6  21.65  21.8  24.55  32.0
EDEDUCWCSC_1998    7.0  16.800000  8.216041  11.4  12.20  13.4  17.15  34.1
EDEDUCWSPR_1998    7.0  34.000000  8.958422  21.0  27.80  35.7  39.25  47.2
EDEDUCWSSC_1998    7.0  11.257143  2.577374   7.8   9.60  10.7  12.90  15.3

In [866]:
# 2003 data
df_2003[[var1e+'_2003', var2e+'_2003', var5e+'_2003', var6e+'_2003']].describe().T

count     mean       std  min     25%    50%    75%   max
EDEDUCMCPR_2003    8.0  21.5375  7.576456  8.8  18.750  20.60  24.65  32.9
EDEDUCMCSC_2003    8.0  15.4125  5.749643  7.2  12.500  14.50  17.95  26.3
EDEDUCWCPR_2003    8.0  22.4250  9.690017  1.8  21.100  22.90  27.10  33.6
EDEDUCWCSC_2003    8.0  11.4000  7.759786  0.3   7.575  10.15  13.05  26.1

In [867]:
#2022 data
df_educ_2022_grp[[var1e+'_2022', var2e+'_2022', var5e+'_2022', var6e+'_2022']].describe().T

count       mean       std        min        25%        50%  \
EDEDUCMCPR_2022    8.0  17.053199  4.654302   9.700000  14.128571  18.693750   
EDEDUCMCSC_2022    8.0  20.073423  5.318132  14.850000  17.356250  18.043333   
EDEDUCWCPR_2022    8.0  18.129122  5.981511   5.300000  16.242857  20.175000   
EDEDUCWCSC_2022    8.0  17.527619  6.591689   7.566667  14.906250  16.562500   

                       75%        max  
EDEDUCMCPR_2022  20.185000  22.560000  
EDEDUCMCSC_2022  20.936786  30.900000  
EDEDUCWCPR_2022  21.804375  23.333333  
EDEDUCWCSC_2022  19.370714  28.600000

#### 2. Health

In [868]:
# 1998 data
df_health_1998[[var1h+'_1998', var2h+'_1998', var3h+'_1998', var4h+'_1998', var5h+'_1998', var6h+'_1998', var7h+'_1998', var8h+'_1998', var9h+'_1998']].describe().T

count       mean        std   min    25%   50%     75%    max
CHVACCCBAS_1998    7.0  59.942857  10.941337  44.4  50.60  66.9   68.15   70.8
CMECMRCCMR_1998    7.0  34.285714  24.376999   6.0  22.00  26.0   45.50   73.0
CMECMRCIMR_1998    7.0  62.857143  34.839769  27.0  45.50  53.0   67.00  135.0
CMECMRCNNR_1998    7.0  24.857143   7.081162  18.0  19.50  23.0   28.00   38.0
CMECMRCPNR_1998    7.0  38.285714  28.511485  10.0  22.00  31.0   43.00   97.0
CMECMRCU5M_1998    7.0  94.571429  53.615474  33.0  67.00  78.0  109.00  199.0
CNNUTSCHA2_1998    7.0  37.242857   5.268414  28.7  34.60  36.6   41.45   43.3
CNNUTSCWA2_1998    7.0  16.771429   5.510812   7.7  13.55  18.7   20.60   22.7
CNNUTSCWH2_1998    7.0   6.657143   1.586250   4.8   5.40   6.1    8.25    8.4

In [869]:
# 2003 data
df_2003[[var1h+'_2003', var2h+'_2003', var7h+'_2003', var8h+'_2003']].describe().T

count     mean        std   min     25%   50%    75%   max
CHVACCCBAS_2003    8.0  48.0250  19.954573   7.5  42.225  53.2  60.00  70.8
CMECMRCCMR_2003    8.0  45.0000  28.804762  10.0  26.000  35.5  72.25  84.0
CNNUTSCHA2_2003    8.0  33.9125   5.971943  23.5  30.300  35.7  37.55  41.2
CNNUTSCWA2_2003    8.0  16.1375   7.125796   5.4  11.675  16.6  18.85  29.6

In [870]:
# 2022 data
df_health_2022_grp[[var1h+'_2022', var2h+'_2022', var7h+'_2022', var8h+'_2022']].describe().T

count       mean        std        min        25%        50%  \
CHVACCCBAS_2022    8.0  76.146920  17.872845  33.533333  76.935714  80.478750   
CMECMRCCMR_2022    8.0   8.784970   5.011133   4.000000   5.943750   6.952381   
CNNUTSCHA2_2022    8.0  16.365759   3.997181  11.100000  13.820000  14.879167   
CNNUTSCWA2_2022    8.0  10.361562   5.033380   5.120000   5.425000  10.056250   

                       75%        max  
CHVACCCBAS_2022  84.775000  89.175000  
CMECMRCCMR_2022   9.575000  17.750000  
CNNUTSCHA2_2022  20.141518  22.080000  
CNNUTSCWA2_2022  14.495000  17.833333

## Data Visualization

# Econometric Analysis

## Differences-in-Differences Regression

In [820]:
# educ: 1,2,5,6
# health: 1,2,7,8

In [941]:
# Define function for creabting the regression table
def create_reg_table1(var, new_var, x1, x2=None):
    restricted_prov_outcome.dropna(inplace=True)
    # Pre-treatment data
    if (x2 != None):
        cols = [var + '_2003', x1, x2]
    else:
        cols = [var + '_2003', x1]
    df_before = restricted_prov_outcome[cols]
    df_before['t'] = 0
    df_before.rename({var + '_2003': new_var}, axis=1, inplace=True)

    # Post-treatment data
    if (x2 != None):
        cols = [var + '_2022', x1, x2]
    else:
        cols = [var + '_2022', x1]
    df_after = restricted_prov_outcome[cols]
    df_after['t'] = 1
    df_after.rename({var + '_2022': new_var}, axis=1, inplace=True)

    # Merged data
    df_reg = pd.concat([df_before, df_after])
    
    return df_reg

### 1. Education

In [944]:
# Run regressions

# var1
m11 = ols('educ ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table1(var1e, 'educ', 'num_med', 'num_high')).fit(cov_type='HC1')
m12 = ols('educ ~ treat + t + treat*t', data=create_reg_table1(var1e, 'educ', 'treat')).fit(cov_type='HC1')
m13 = ols('educ ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table1(var1e, 'educ', 'cov_med', 'cov_high')).fit(cov_type='HC1')

# var2
m21 = ols('educ ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table1(var2e, 'educ', 'num_med', 'num_high')).fit(cov_type='HC1')
m22 = ols('educ ~ treat + t + treat*t', data=create_reg_table1(var2e, 'educ', 'treat')).fit(cov_type='HC1')
m23 = ols('educ ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table1(var2e, 'educ', 'cov_med', 'cov_high')).fit(cov_type='HC1')

#var3
m31 = ols('educ ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table1(var3e, 'educ', 'num_med', 'num_high')).fit(cov_type='HC1')
m32 = ols('educ ~ treat + t + treat*t', data=create_reg_table1(var3e, 'educ', 'treat')).fit(cov_type='HC1')
m33 = ols('educ ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table1(var3e, 'educ', 'cov_med', 'cov_high')).fit(cov_type='HC1')

#var4
m41 = ols('educ ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table1(var4e, 'educ', 'num_med', 'num_high')).fit(cov_type='HC1')
m42 = ols('educ ~ treat + t + treat*t', data=create_reg_table1(var4e, 'educ', 'treat')).fit(cov_type='HC1')
m43 = ols('educ ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table1(var4e, 'educ', 'cov_med', 'cov_high')).fit(cov_type='HC1')

#var5
m51 = ols('educ ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table1(var5e, 'educ', 'num_med', 'num_high')).fit(cov_type='HC1')
m52 = ols('educ ~ treat + t + treat*t', data=create_reg_table1(var5e, 'educ', 'treat')).fit(cov_type='HC1')
m53 = ols('educ ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table1(var5e, 'educ', 'cov_med', 'cov_high')).fit(cov_type='HC1')

#var6
m61 = ols('educ ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table1(var6e, 'educ', 'num_med', 'num_high')).fit(cov_type='HC1')
m62 = ols('educ ~ treat + t + treat*t', data=create_reg_table1(var6e, 'educ', 'treat')).fit(cov_type='HC1')
m63 = ols('educ ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table1(var6e, 'educ', 'cov_med', 'cov_high')).fit(cov_type='HC1')

#var7
m71 = ols('educ ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table1(var7e, 'educ', 'num_med', 'num_high')).fit(cov_type='HC1')
m72 = ols('educ ~ treat + t + treat*t', data=create_reg_table1(var7e, 'educ', 'treat')).fit(cov_type='HC1')
m73 = ols('educ ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table1(var7e, 'educ', 'cov_med', 'cov_high')).fit(cov_type='HC1')

#var8
m81 = ols('educ ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table1(var8e, 'educ', 'num_med', 'num_high')).fit(cov_type='HC1')
m82 = ols('educ ~ treat + t + treat*t', data=create_reg_table1(var8e, 'educ', 'treat')).fit(cov_type='HC1')
m83 = ols('educ ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table1(var8e, 'educ', 'cov_med', 'cov_high')).fit(cov_type='HC1')

In [956]:
m11.mse_resid

42.62214865480917

In [957]:
m13.mse_resid

120.74527793524815

In [946]:
# Variable 1 results
print(m11.summary())
print(m13.summary())

                            OLS Regression Results                            
Dep. Variable:                   educ   R-squared:                       0.453
Model:                            OLS   Adj. R-squared:                 -0.002
Method:                 Least Squares   F-statistic:                     1.371
Date:                Fri, 26 Apr 2024   Prob (F-statistic):              0.352
Time:                        14:03:46   Log-Likelihood:                -32.242
No. Observations:                  12   AIC:                             76.48
Df Residuals:                       6   BIC:                             79.39
Df Model:                           5                                         
Covariance Type:                  HC1                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept     26.6000      3.900      6.821      0.0

In [958]:
m21.mse_resid

94.88241177721089

In [959]:
m23.mse_resid

746.6460430839002

In [948]:
# Variable 1 results
print(m21.summary())
print(m23.summary())

                            OLS Regression Results                            
Dep. Variable:                   educ   R-squared:                       0.617
Model:                            OLS   Adj. R-squared:                  0.297
Method:                 Least Squares   F-statistic:                     5.401
Date:                Fri, 26 Apr 2024   Prob (F-statistic):             0.0317
Time:                        14:03:52   Log-Likelihood:                -26.384
No. Observations:                  12   AIC:                             64.77
Df Residuals:                       6   BIC:                             67.68
Df Model:                           5                                         
Covariance Type:                  HC1                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept     16.6500      0.950     17.526      0.0

In [960]:
m51.mse_resid

238.12896258503403

In [961]:
m53.mse_resid

854.5909977324262

In [949]:
# Variable 1 results
print(m51.summary())
print(m53.summary())

                            OLS Regression Results                            
Dep. Variable:                   educ   R-squared:                       0.919
Model:                            OLS   Adj. R-squared:                  0.852
Method:                 Least Squares   F-statistic:                     19.46
Date:                Fri, 26 Apr 2024   Prob (F-statistic):            0.00120
Time:                        14:04:11   Log-Likelihood:                -20.435
No. Observations:                  12   AIC:                             52.87
Df Residuals:                       6   BIC:                             55.78
Df Model:                           5                                         
Covariance Type:                  HC1                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept     22.9000      1.000     22.900      0.0

In [962]:
m61.mse_resid

544.1518920068028

In [963]:
m63.mse_resid

2470.224348072562

In [950]:
# Variable 1 results
print(m61.summary())
print(m63.summary())

                            OLS Regression Results                            
Dep. Variable:                   educ   R-squared:                       0.717
Model:                            OLS   Adj. R-squared:                  0.481
Method:                 Least Squares   F-statistic:                     34.10
Date:                Fri, 26 Apr 2024   Prob (F-statistic):           0.000248
Time:                        14:04:13   Log-Likelihood:                -28.581
No. Observations:                  12   AIC:                             69.16
Df Residuals:                       6   BIC:                             72.07
Df Model:                           5                                         
Covariance Type:                  HC1                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept     10.6000      0.700     15.143      0.0

### 2. Health

In [973]:
# Run regressions

# var1
m11 = ols('health ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table1(var1h, 'health', 'num_med', 'num_high')).fit(cov_type='HC1')
m12 = ols('health ~ treat + t + treat*t', data=create_reg_table1(var1h, 'health', 'treat')).fit(cov_type='HC1')
m13 = ols('health ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table1(var1h, 'health', 'cov_med', 'cov_high')).fit(cov_type='HC1')

# var2
m21 = ols('health ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table1(var2h, 'health', 'num_med', 'num_high')).fit(cov_type='HC1')
m22 = ols('health ~ treat + t + treat*t', data=create_reg_table1(var2h, 'health', 'treat')).fit(cov_type='HC1')
m23 = ols('health ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table1(var2h, 'health', 'cov_med', 'cov_high')).fit(cov_type='HC1')

# var3
m31 = ols('health ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table1(var3h, 'health', 'num_med', 'num_high')).fit(cov_type='HC1')
m32 = ols('health ~ treat + t + treat*t', data=create_reg_table1(var3h, 'health', 'treat')).fit(cov_type='HC1')
m33 = ols('health ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table1(var3h, 'health', 'cov_med', 'cov_high')).fit(cov_type='HC1')

# var4
m41 = ols('health ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table1(var4h, 'health', 'num_med', 'num_high')).fit(cov_type='HC1')
m42 = ols('health ~ treat + t + treat*t', data=create_reg_table1(var4h, 'health', 'treat')).fit(cov_type='HC1')
m43 = ols('health ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table1(var4h, 'health', 'cov_med', 'cov_high')).fit(cov_type='HC1')

# var5
m51 = ols('health ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table1(var5h, 'health', 'num_med', 'num_high')).fit(cov_type='HC1')
m52 = ols('health ~ treat + t + treat*t', data=create_reg_table1(var5h, 'health', 'treat')).fit(cov_type='HC1')
m53 = ols('health ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table1(var5h, 'health', 'cov_med', 'cov_high')).fit(cov_type='HC1')

# var6
m61 = ols('health ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table1(var6h, 'health', 'num_med', 'num_high')).fit(cov_type='HC1')
m62 = ols('health ~ treat + t + treat*t', data=create_reg_table1(var6h, 'health', 'treat')).fit(cov_type='HC1')
m63 = ols('health ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table1(var6h, 'health', 'cov_med', 'cov_high')).fit(cov_type='HC1')

# var7
m71 = ols('health ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table1(var7h, 'health', 'num_med', 'num_high')).fit(cov_type='HC1')
m72 = ols('health ~ treat + t + treat*t', data=create_reg_table1(var7h, 'health', 'treat')).fit(cov_type='HC1')
m73 = ols('health ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table1(var7h, 'health', 'cov_med', 'cov_high')).fit(cov_type='HC1')

# var8
m81 = ols('health ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table1(var8h, 'health', 'num_med', 'num_high')).fit(cov_type='HC1')
m82 = ols('health ~ treat + t + treat*t', data=create_reg_table1(var8h, 'health', 'treat')).fit(cov_type='HC1')
m83 = ols('health ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table1(var8h, 'health', 'cov_med', 'cov_high')).fit(cov_type='HC1')

# var9
m91 = ols('health ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table1(var9h, 'health', 'num_med', 'num_high')).fit(cov_type='HC1')
m92 = ols('health ~ treat + t + treat*t', data=create_reg_table1(var9h, 'health', 'treat')).fit(cov_type='HC1')
m93 = ols('health ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table1(var9h, 'health', 'cov_med', 'cov_high')).fit(cov_type='HC1')

In [980]:
var8h

'CNNUTSCWA2'

In [974]:
m11.mse_resid

42.62214865480917

In [975]:
m13.mse_resid

120.74527793524815

In [976]:
# Variable 1 results
print(m11.summary())
print(m13.summary())

                            OLS Regression Results                            
Dep. Variable:                 health   R-squared:                       0.930
Model:                            OLS   Adj. R-squared:                  0.871
Method:                 Least Squares   F-statistic:                     13.95
Date:                Fri, 26 Apr 2024   Prob (F-statistic):            0.00298
Time:                        14:33:07   Log-Likelihood:                -35.383
No. Observations:                  12   AIC:                             82.77
Df Residuals:                       6   BIC:                             85.67
Df Model:                           5                                         
Covariance Type:                  HC1                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept     56.8000      5.300     10.717      0.0

In [966]:
m21.mse_resid

94.88241177721089

In [967]:
m23.mse_resid

746.6460430839002

In [953]:
# Variable 1 results
print(m21.summary())
print(m23.summary())

                            OLS Regression Results                            
Dep. Variable:                 health   R-squared:                       0.925
Model:                            OLS   Adj. R-squared:                  0.862
Method:                 Least Squares   F-statistic:                     38.59
Date:                Fri, 26 Apr 2024   Prob (F-statistic):           0.000174
Time:                        14:04:17   Log-Likelihood:                -40.184
No. Observations:                  12   AIC:                             92.37
Df Residuals:                       6   BIC:                             95.28
Df Model:                           5                                         
Covariance Type:                  HC1                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept     29.0000     12.000      2.417      0.0

In [968]:
m71.mse_resid

10.880975922382847

In [969]:
m73.mse_resid

6.977430032753838

In [954]:
# Variable 1 results
print(m71.summary())
print(m73.summary())

                            OLS Regression Results                            
Dep. Variable:                 health   R-squared:                       0.946
Model:                            OLS   Adj. R-squared:                  0.901
Method:                 Least Squares   F-statistic:                     218.0
Date:                Fri, 26 Apr 2024   Prob (F-statistic):           1.07e-06
Time:                        14:04:18   Log-Likelihood:                -27.190
No. Observations:                  12   AIC:                             66.38
Df Residuals:                       6   BIC:                             69.29
Df Model:                           5                                         
Covariance Type:                  HC1                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept     39.1000      2.100     18.619      0.0

In [970]:
m81.mse_resid

9.110706307870371

In [971]:
m83.mse_resid

14.414911419753084

In [955]:
# Variable 1 results
print(m81.summary())
print(m83.summary())

                            OLS Regression Results                            
Dep. Variable:                 health   R-squared:                       0.782
Model:                            OLS   Adj. R-squared:                  0.601
Method:                 Least Squares   F-statistic:                     269.3
Date:                Fri, 26 Apr 2024   Prob (F-statistic):           5.70e-07
Time:                        14:04:19   Log-Likelihood:                -26.125
No. Observations:                  12   AIC:                             64.25
Df Residuals:                       6   BIC:                             67.16
Df Model:                           5                                         
Covariance Type:                  HC1                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept     18.9000      0.100    189.000      0.0

---

In [983]:
var1h, var2h, var7h, var8h

('CHVACCCBAS', 'CMECMRCCMR', 'CNNUTSCHA2', 'CNNUTSCWA2')

## Parallel Trends

In [996]:
# Define function for creabting the regression table
def create_reg_table(var, new_var, x1, x2=None):
    restricted_prov_outcome.dropna(inplace=True)
    # Pre-treatment data
    if (x2 != None):
        cols = [var + '_1998', x1, x2]
    else:
        cols = [var + '_1998', x1]
    df_before = restricted_prov_outcome[cols]
    df_before['t'] = 0
    df_before.rename({var + '_1998': new_var}, axis=1, inplace=True)

    # Post-treatment data
    if (x2 != None):
        cols = [var + '_2003', x1, x2]
    else:
        cols = [var + '_2003', x1]
    df_after = restricted_prov_outcome[cols]
    df_after['t'] = 1
    df_after.rename({var + '_2003': new_var}, axis=1, inplace=True)

    # Merged data
    df_reg = pd.concat([df_before, df_after])
    
    return df_reg

In [1003]:
# Run regressions

# var1
m11 = ols('educ ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table(var1e, 'educ', 'num_med', 'num_high')).fit(cov_type='HC1')
m12 = ols('educ ~ treat + t + treat*t', data=create_reg_table(var1e, 'educ', 'treat')).fit(cov_type='HC1')
m13 = ols('educ ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table(var1e, 'educ', 'cov_med', 'cov_high')).fit(cov_type='HC1')

# var2
m21 = ols('educ ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table(var2e, 'educ', 'num_med', 'num_high')).fit(cov_type='HC1')
m22 = ols('educ ~ treat + t + treat*t', data=create_reg_table(var2e, 'educ', 'treat')).fit(cov_type='HC1')
m23 = ols('educ ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table(var2e, 'educ', 'cov_med', 'cov_high')).fit(cov_type='HC1')

#var3
m31 = ols('educ ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table(var3e, 'educ', 'num_med', 'num_high')).fit(cov_type='HC1')
m32 = ols('educ ~ treat + t + treat*t', data=create_reg_table(var3e, 'educ', 'treat')).fit(cov_type='HC1')
m33 = ols('educ ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table(var3e, 'educ', 'cov_med', 'cov_high')).fit(cov_type='HC1')

#var4
m41 = ols('educ ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table(var4e, 'educ', 'num_med', 'num_high')).fit(cov_type='HC1')
m42 = ols('educ ~ treat + t + treat*t', data=create_reg_table(var4e, 'educ', 'treat')).fit(cov_type='HC1')
m43 = ols('educ ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table(var4e, 'educ', 'cov_med', 'cov_high')).fit(cov_type='HC1')

#var5
m51 = ols('educ ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table(var5e, 'educ', 'num_med', 'num_high')).fit(cov_type='HC1')
m52 = ols('educ ~ treat + t + treat*t', data=create_reg_table(var5e, 'educ', 'treat')).fit(cov_type='HC1')
m53 = ols('educ ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table(var5e, 'educ', 'cov_med', 'cov_high')).fit(cov_type='HC1')

#var6
m61 = ols('educ ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table(var6e, 'educ', 'num_med', 'num_high')).fit(cov_type='HC1')
m62 = ols('educ ~ treat + t + treat*t', data=create_reg_table(var6e, 'educ', 'treat')).fit(cov_type='HC1')
m63 = ols('educ ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table(var6e, 'educ', 'cov_med', 'cov_high')).fit(cov_type='HC1')

#var7
m71 = ols('educ ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table(var7e, 'educ', 'num_med', 'num_high')).fit(cov_type='HC1')
m72 = ols('educ ~ treat + t + treat*t', data=create_reg_table(var7e, 'educ', 'treat')).fit(cov_type='HC1')
m73 = ols('educ ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table(var7e, 'educ', 'cov_med', 'cov_high')).fit(cov_type='HC1')

#var8
m81 = ols('educ ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table(var8e, 'educ', 'num_med', 'num_high')).fit(cov_type='HC1')
m82 = ols('educ ~ treat + t + treat*t', data=create_reg_table(var8e, 'educ', 'treat')).fit(cov_type='HC1')
m83 = ols('educ ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table(var8e, 'educ', 'cov_med', 'cov_high')).fit(cov_type='HC1')

In [1007]:
m11.mse_resid, m13.mse_resid

(26.954166666666662, 37.11111111111111)

In [1004]:
print(m11.summary())
print(m13.summary())

                            OLS Regression Results                            
Dep. Variable:                   educ   R-squared:                       0.498
Model:                            OLS   Adj. R-squared:                  0.080
Method:                 Least Squares   F-statistic:                     9.098
Date:                Fri, 26 Apr 2024   Prob (F-statistic):            0.00906
Time:                        17:01:20   Log-Likelihood:                -32.633
No. Observations:                  12   AIC:                             77.27
Df Residuals:                       6   BIC:                             80.18
Df Model:                           5                                         
Covariance Type:                  HC1                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept     26.7000      1.000     26.700      0.0

In [1008]:
m21.mse_resid, m23.mse_resid

(9.996666666666671, 7.073055555555555)

In [1005]:
print(m21.summary())
print(m23.summary())

                            OLS Regression Results                            
Dep. Variable:                   educ   R-squared:                       0.756
Model:                            OLS   Adj. R-squared:                  0.553
Method:                 Least Squares   F-statistic:                     7.403
Date:                Fri, 26 Apr 2024   Prob (F-statistic):             0.0151
Time:                        17:01:22   Log-Likelihood:                -26.682
No. Observations:                  12   AIC:                             65.36
Df Residuals:                       6   BIC:                             68.27
Df Model:                           5                                         
Covariance Type:                  HC1                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept     23.1000      2.200     10.500      0.0

In [1010]:
m51.mse_resid, m53.mse_resid

(6.538333333333333, 41.996388888888895)

In [1001]:
print(m51.summary())
print(m53.summary())

                            OLS Regression Results                            
Dep. Variable:                   educ   R-squared:                       0.877
Model:                            OLS   Adj. R-squared:                  0.774
Method:                 Least Squares   F-statistic:                     25.20
Date:                Fri, 26 Apr 2024   Prob (F-statistic):           0.000585
Time:                        17:01:09   Log-Likelihood:                -24.134
No. Observations:                  12   AIC:                             60.27
Df Residuals:                       6   BIC:                             63.18
Df Model:                           5                                         
Covariance Type:                  HC1                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept     21.7500      0.050    435.000      0.0

In [1012]:
m61.mse_resid, m63.mse_resid

(9.299166666666666, 17.20305555555556)

In [1002]:
print(m61.summary())
print(m63.summary())

                            OLS Regression Results                            
Dep. Variable:                   educ   R-squared:                       0.662
Model:                            OLS   Adj. R-squared:                  0.380
Method:                 Least Squares   F-statistic:                     27.68
Date:                Fri, 26 Apr 2024   Prob (F-statistic):           0.000449
Time:                        17:01:13   Log-Likelihood:                -26.248
No. Observations:                  12   AIC:                             64.50
Df Residuals:                       6   BIC:                             67.41
Df Model:                           5                                         
Covariance Type:                  HC1                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept     12.8000      0.600     21.333      0.0

In [986]:
# Run regressions

# var1
m11 = ols('health ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table(var1h, 'health', 'num_med', 'num_high')).fit(cov_type='HC1')
m12 = ols('health ~ treat + t + treat*t', data=create_reg_table(var1h, 'health', 'treat')).fit(cov_type='HC1')
m13 = ols('health ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table(var1h, 'health', 'cov_med', 'cov_high')).fit(cov_type='HC1')

# var2
m21 = ols('health ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table(var2h, 'health', 'num_med', 'num_high')).fit(cov_type='HC1')
m22 = ols('health ~ treat + t + treat*t', data=create_reg_table(var2h, 'health', 'treat')).fit(cov_type='HC1')
m23 = ols('health ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table(var2h, 'health', 'cov_med', 'cov_high')).fit(cov_type='HC1')

# var3
m31 = ols('health ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table(var3h, 'health', 'num_med', 'num_high')).fit(cov_type='HC1')
m32 = ols('health ~ treat + t + treat*t', data=create_reg_table(var3h, 'health', 'treat')).fit(cov_type='HC1')
m33 = ols('health ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table(var3h, 'health', 'cov_med', 'cov_high')).fit(cov_type='HC1')

# var4
m41 = ols('health ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table(var4h, 'health', 'num_med', 'num_high')).fit(cov_type='HC1')
m42 = ols('health ~ treat + t + treat*t', data=create_reg_table(var4h, 'health', 'treat')).fit(cov_type='HC1')
m43 = ols('health ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table(var4h, 'health', 'cov_med', 'cov_high')).fit(cov_type='HC1')

# var5
m51 = ols('health ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table(var5h, 'health', 'num_med', 'num_high')).fit(cov_type='HC1')
m52 = ols('health ~ treat + t + treat*t', data=create_reg_table(var5h, 'health', 'treat')).fit(cov_type='HC1')
m53 = ols('health ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table(var5h, 'health', 'cov_med', 'cov_high')).fit(cov_type='HC1')

# var6
m61 = ols('health ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table(var6h, 'health', 'num_med', 'num_high')).fit(cov_type='HC1')
m62 = ols('health ~ treat + t + treat*t', data=create_reg_table(var6h, 'health', 'treat')).fit(cov_type='HC1')
m63 = ols('health ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table(var6h, 'health', 'cov_med', 'cov_high')).fit(cov_type='HC1')

# var7
m71 = ols('health ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table(var7h, 'health', 'num_med', 'num_high')).fit(cov_type='HC1')
m72 = ols('health ~ treat + t + treat*t', data=create_reg_table(var7h, 'health', 'treat')).fit(cov_type='HC1')
m73 = ols('health ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table(var7h, 'health', 'cov_med', 'cov_high')).fit(cov_type='HC1')

# var8
m81 = ols('health ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table(var8h, 'health', 'num_med', 'num_high')).fit(cov_type='HC1')
m82 = ols('health ~ treat + t + treat*t', data=create_reg_table(var8h, 'health', 'treat')).fit(cov_type='HC1')
m83 = ols('health ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table(var8h, 'health', 'cov_med', 'cov_high')).fit(cov_type='HC1')

# var9
m91 = ols('health ~ num_med + num_high + t + num_med*t + num_high*t', data=create_reg_table(var9h, 'health', 'num_med', 'num_high')).fit(cov_type='HC1')
m92 = ols('health ~ treat + t + treat*t', data=create_reg_table(var9h, 'health', 'treat')).fit(cov_type='HC1')
m93 = ols('health ~ cov_med + cov_high + t + cov_med*t + cov_high*t', data=create_reg_table(var9h, 'health', 'cov_med', 'cov_high')).fit(cov_type='HC1')

In [922]:
m11.mse_resid

38.135

In [923]:
m13.mse_resid

208.92222222222222

In [988]:
# Variable 1 results
print(m11.summary())
print(m13.summary())

                            OLS Regression Results                            
Dep. Variable:                 health   R-squared:                       0.866
Model:                            OLS   Adj. R-squared:                  0.754
Method:                 Least Squares   F-statistic:                     12.29
Date:                Fri, 26 Apr 2024   Prob (F-statistic):            0.00417
Time:                        16:56:19   Log-Likelihood:                -34.715
No. Observations:                  12   AIC:                             81.43
Df Residuals:                       6   BIC:                             84.34
Df Model:                           5                                         
Covariance Type:                  HC1                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept     67.3000      0.400    168.250      0.0

In [891]:
# Variable 1 results
print(m21.summary())
print(m23.summary())

                            OLS Regression Results                            
Dep. Variable:                 health   R-squared:                       0.891
Model:                            OLS   Adj. R-squared:                  0.801
Method:                 Least Squares   F-statistic:                     15.76
Date:                Fri, 26 Apr 2024   Prob (F-statistic):            0.00214
Time:                        12:32:24   Log-Likelihood:                -42.705
No. Observations:                  12   AIC:                             97.41
Df Residuals:                       6   BIC:                             100.3
Df Model:                           5                                         
Covariance Type:                  HC1                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept     23.0000      5.000      4.600      0.0

In [938]:
m53.mse_resid

1507.5277777777776

In [892]:
# Variable 1 results
print(m51.summary())
print(m53.summary())

                            OLS Regression Results                            
Dep. Variable:                 health   R-squared:                       0.681
Model:                            OLS   Adj. R-squared:                  0.415
Method:                 Least Squares   F-statistic:                     2.146
Date:                Fri, 26 Apr 2024   Prob (F-statistic):              0.190
Time:                        12:32:24   Log-Likelihood:                -50.606
No. Observations:                  12   AIC:                             113.2
Df Residuals:                       6   BIC:                             116.1
Df Model:                           5                                         
Covariance Type:                  HC1                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept     32.0000     10.000      3.200      0.0

In [939]:
m61.mse_resid

1250.25

In [940]:
m63.mse_resid

4861.5277777777765

In [893]:
# Variable 1 results
print(m61.summary())
print(m63.summary())

                            OLS Regression Results                            
Dep. Variable:                 health   R-squared:                       0.767
Model:                            OLS   Adj. R-squared:                  0.572
Method:                 Least Squares   F-statistic:                     3.094
Date:                Fri, 26 Apr 2024   Prob (F-statistic):              0.101
Time:                        12:32:24   Log-Likelihood:                -55.655
No. Observations:                  12   AIC:                             123.3
Df Residuals:                       6   BIC:                             126.2
Df Model:                           5                                         
Covariance Type:                  HC1                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept     82.0000     14.000      5.857      0.0

In [894]:
# Variable 1 results
print(m11.summary())
print(m13.summary())

                            OLS Regression Results                            
Dep. Variable:                 health   R-squared:                       0.866
Model:                            OLS   Adj. R-squared:                  0.754
Method:                 Least Squares   F-statistic:                     12.29
Date:                Fri, 26 Apr 2024   Prob (F-statistic):            0.00417
Time:                        12:32:24   Log-Likelihood:                -34.715
No. Observations:                  12   AIC:                             81.43
Df Residuals:                       6   BIC:                             84.34
Df Model:                           5                                         
Covariance Type:                  HC1                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept     67.3000      0.400    168.250      0.0

In [895]:
# Variable 1 results
print(m21.summary())
print(m23.summary())

                            OLS Regression Results                            
Dep. Variable:                 health   R-squared:                       0.891
Model:                            OLS   Adj. R-squared:                  0.801
Method:                 Least Squares   F-statistic:                     15.76
Date:                Fri, 26 Apr 2024   Prob (F-statistic):            0.00214
Time:                        12:32:24   Log-Likelihood:                -42.705
No. Observations:                  12   AIC:                             97.41
Df Residuals:                       6   BIC:                             100.3
Df Model:                           5                                         
Covariance Type:                  HC1                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept     23.0000      5.000      4.600      0.0

In [896]:
# Variable 1 results
print(m71.summary())
print(m73.summary())

                            OLS Regression Results                            
Dep. Variable:                 health   R-squared:                       0.223
Model:                            OLS   Adj. R-squared:                 -0.425
Method:                 Least Squares   F-statistic:                     1.083
Date:                Fri, 26 Apr 2024   Prob (F-statistic):              0.454
Time:                        12:32:24   Log-Likelihood:                -30.816
No. Observations:                  12   AIC:                             73.63
Df Residuals:                       6   BIC:                             76.54
Df Model:                           5                                         
Covariance Type:                  HC1                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept     39.7500      3.150     12.619      0.0

In [987]:
# Variable 1 results
print(m81.summary())
print(m83.summary())

                            OLS Regression Results                            
Dep. Variable:                 health   R-squared:                       0.412
Model:                            OLS   Adj. R-squared:                 -0.078
Method:                 Least Squares   F-statistic:                     2.295
Date:                Fri, 26 Apr 2024   Prob (F-statistic):              0.170
Time:                        16:55:50   Log-Likelihood:                -29.537
No. Observations:                  12   AIC:                             71.07
Df Residuals:                       6   BIC:                             73.98
Df Model:                           5                                         
Covariance Type:                  HC1                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept     20.6000      1.300     15.846      0.0

----